### Which Cities are Similar in Size to Dayton, Ohio?
We'll start by scraping Wikipedia's List of United States cities by Population:

In [367]:
# Library imports
import numpy as np
import pandas as pd
from pandas_profiling import ProfileReport # Pandas profiling is an especially powerful tool for exploratory analysis.
import requests # Used later for importing raw Excel file from GitHub
import io # Used later for importing raw Excel file from GitHub

import json # library to handle JSON files

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

pd.set_option('display.max_columns', 999) # Setting pandas to display all of the columns.
pd.set_option('display.max_rows', 999)

In [2]:
wiki_cities_url = 'https://en.wikipedia.org/wiki/List_of_United_States_cities_by_population'

In [3]:
cities = pd.read_html(wiki_cities_url, header=0)
df_cities = cities[4] # Dataframe pulled from the 4th table on the wikipedia page.
df_cities.head()

2019rank              City    State[c]  2019estimate  2010Census   Change  \
0         1  New York City[d]    New York       8336817     8175133   +1.98%   
1         2       Los Angeles  California       3979576     3792621   +4.93%   
2         3           Chicago    Illinois       2693976     2695598   −0.06%   
3         4        Houston[3]       Texas       2320268     2100263  +10.48%   
4         5           Phoenix     Arizona       1680992     1445632  +16.28%   

  2016 land area 2016 land area.1 2016 population density  \
0    301.5 sq mi        780.9 km2            28,317/sq mi   
1    468.7 sq mi      1,213.9 km2             8,484/sq mi   
2    227.3 sq mi        588.7 km2            11,900/sq mi   
3    637.5 sq mi      1,651.1 km2             3,613/sq mi   
4    517.6 sq mi      1,340.6 km2             3,120/sq mi   

  2016 population density.1                                         Location  
0                10,933/km2    40°39′49″N 73°56′19″W﻿ / ﻿40.6635°N 73.9387°W  
1                 3,276/km2  34°01′10″N 118°24′39″W﻿ / ﻿34.0194°N 118.4108°W  
2                 4,600/km2    41°50′15″N 87°40′54″W﻿ / ﻿41.8376°N 87.6818°W  
3                 1,395/km2    29°47′12″N 95°23′27″W﻿ / ﻿29.7866°N 95.3909°W  
4                 1,200/km2  33°34′20″N 112°05′24″W﻿ / ﻿33.5722°N 112.0901°W

In [4]:
df_cities.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 317 entries, 0 to 316
Data columns (total 11 columns):
 #   Column                     Non-Null Count  Dtype 
---  ------                     --------------  ----- 
 0   2019rank                   317 non-null    int64 
 1   City                       317 non-null    object
 2   State[c]                   317 non-null    object
 3   2019estimate               317 non-null    int64 
 4   2010Census                 317 non-null    int64 
 5   Change                     317 non-null    object
 6   2016 land area             317 non-null    object
 7   2016 land area.1           317 non-null    object
 8   2016 population density    317 non-null    object
 9   2016 population density.1  317 non-null    object
 10  Location                   317 non-null    object
dtypes: int64(3), object(8)
memory usage: 27.4+ KB


Let's drop irrelevant and redundant columns from the cities dataframe:

In [5]:
# Drop unwanted columns:
drop_columns = ['2019rank','2016 land area.1','2016 population density','2016 population density.1','Location']
df_cities.drop(drop_columns, axis=1, inplace=True)
df_cities.head()

City    State[c]  2019estimate  2010Census   Change  \
0  New York City[d]    New York       8336817     8175133   +1.98%   
1       Los Angeles  California       3979576     3792621   +4.93%   
2           Chicago    Illinois       2693976     2695598   −0.06%   
3        Houston[3]       Texas       2320268     2100263  +10.48%   
4           Phoenix     Arizona       1680992     1445632  +16.28%   

  2016 land area  
0    301.5 sq mi  
1    468.7 sq mi  
2    227.3 sq mi  
3    637.5 sq mi  
4    517.6 sq mi

The cities dataframe above is in need of some cleaning.\
We'll remove unwanted bracketed notes from the **City** column values, i.e. New York City[d].\
We will also remove the + and % signs from the **Change** column values.\
In the **Change** column, we'll need to replace the non-ASCII dashes with hyphens for float type conversion.\
Lastly, we will remove the "sq mi" text from the **2016 land area** column values, then change the values to float type as well.

In [6]:
# Removing bracketed notes from City column:
df_cities['City'] = df_cities['City'].str.replace(r'\[.*\]','') # Removes bracketed notes.
df_cities.head()

City    State[c]  2019estimate  2010Census   Change 2016 land area
0  New York City    New York       8336817     8175133   +1.98%    301.5 sq mi
1    Los Angeles  California       3979576     3792621   +4.93%    468.7 sq mi
2        Chicago    Illinois       2693976     2695598   −0.06%    227.3 sq mi
3        Houston       Texas       2320268     2100263  +10.48%    637.5 sq mi
4        Phoenix     Arizona       1680992     1445632  +16.28%    517.6 sq mi

In [7]:
# Removing % and + signs from Change column:
df_cities['Change'] = df_cities['Change'].str.replace(r'\%','') # Removes % sign.
df_cities['Change'] = df_cities['Change'].str.replace(r'\+','') # Removes + sign.

# Replacing non-ASCII characters with hyphen in Change column.
df_cities['Change'] = df_cities['Change'].str.replace(r'[^\x00-\x7F]+','-')

At this point, I attempted to convert the **Change** column to float type, but found that there was a non-numerical data point corresponding to the city of Jurupa Valley, California.

The Wikipedia footnote says "Jurupa Valley was incorporated as a city on July 1, 2011, from various portions of unincorporated territory in Riverside County, California. Because of this, there is no official 2010 Census population."

A city that grows from 0 population would be considered to have infinite growth, and therefore Jarupa Valley should be dropped from the dataframe to prevent analysis problems.

In [8]:
df_cities.drop(df_cities[(df_cities['City'] == 'Jurupa Valley')].index, inplace=True) # Dropping Jurupa Valley.
df_cities.reset_index(drop=True,inplace=True)
df_cities.shape # Did this to confirm that a row was dropped - the number of rows should now be 316.

(316, 6)

Now we should be able to convert the **Change** column to the float type.

In [9]:
df_cities['Change'] = df_cities['Change'].astype(float)

Lastly, let's clean up the **2016 land area** column.

In [10]:
df_cities['2016 land area'] = df_cities['2016 land area'].str.replace(r'[^0-9.]+','').astype(float)

And let's rename the columns while we're at it.

In [11]:
old_columns = ['State[c]','2019estimate','2010Census','Change','2016 land area']
new_columns = ['State','Pop 2019 Est','Pop 2010','Pop Change %','2016 Land SqMi']
df_cities[new_columns] = df_cities[old_columns]
df_cities.drop(old_columns,axis=1,inplace=True)
df_cities.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 316 entries, 0 to 315
Data columns (total 6 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   City            316 non-null    object 
 1   State           316 non-null    object 
 2   Pop 2019 Est    316 non-null    int64  
 3   Pop 2010        316 non-null    int64  
 4   Pop Change %    316 non-null    float64
 5   2016 Land SqMi  316 non-null    float64
dtypes: float64(2), int64(2), object(2)
memory usage: 14.9+ KB


In [12]:
df_cities

City       State  Pop 2019 Est  Pop 2010  Pop Change %  \
0    New York City    New York       8336817   8175133          1.98   
1      Los Angeles  California       3979576   3792621          4.93   
2          Chicago    Illinois       2693976   2695598         -0.06   
3          Houston       Texas       2320268   2100263         10.48   
4          Phoenix     Arizona       1680992   1445632         16.28   
..             ...         ...           ...       ...           ...   
311     San Angelo       Texas        101004     93200          8.37   
312      Vacaville  California        100670     92428          8.92   
313        Clinton    Michigan        100471     96796          3.80   
314           Bend      Oregon        100421     76639         31.03   
315     Woodbridge  New Jersey        100145     99585          0.56   

     2016 Land SqMi  
0             301.5  
1             468.7  
2             227.3  
3             637.5  
4             517.6  
..              ...  
311            59.9  
312            29.0  
313            28.1  
314            33.1  
315            23.3  

[316 rows x 6 columns]

Recall earlier that we dropped the 2016 population density columns. We're going to add two calculated columns in their place based on the 2010 and 2019 population figures. We'll be assuming that the land area has not significantly changed relative to the 2016 data (we don't have available data to suggest otherwise).
1. Density 2010  = Pop 2010 / 2016 Land SqMi
2. Density 2019 Est = Pop 2019 Est / 2016 Land SqMi

In [13]:
df_cities['Density 2010'] = (df_cities['Pop 2010']/df_cities['2016 Land SqMi'])
df_cities['Density 2019 Est'] = (df_cities['Pop 2019 Est']/df_cities['2016 Land SqMi'])

In [14]:
df_cities

City       State  Pop 2019 Est  Pop 2010  Pop Change %  \
0    New York City    New York       8336817   8175133          1.98   
1      Los Angeles  California       3979576   3792621          4.93   
2          Chicago    Illinois       2693976   2695598         -0.06   
3          Houston       Texas       2320268   2100263         10.48   
4          Phoenix     Arizona       1680992   1445632         16.28   
..             ...         ...           ...       ...           ...   
311     San Angelo       Texas        101004     93200          8.37   
312      Vacaville  California        100670     92428          8.92   
313        Clinton    Michigan        100471     96796          3.80   
314           Bend      Oregon        100421     76639         31.03   
315     Woodbridge  New Jersey        100145     99585          0.56   

     2016 Land SqMi  Density 2010  Density 2019 Est  
0             301.5  27114.868988      27651.134328  
1             468.7   8091.787924       8490.667805  
2             227.3  11859.208095      11852.072151  
3             637.5   3294.530196       3639.636078  
4             517.6   2792.952087       3247.666151  
..              ...           ...               ...  
311            59.9   1555.926544       1686.210351  
312            29.0   3187.172414       3471.379310  
313            28.1   3444.697509       3575.480427  
314            33.1   2315.377644       3033.867069  
315            23.3   4274.034335       4298.068670  

[316 rows x 8 columns]

Let's change the Pop Change % Column to a proportion value. Later on, this will simplify comparisons with QuickFacts census data.

In [15]:
df_cities['Pop Change Prop.'] = df_cities['Pop Change %']/100
df_cities.drop('Pop Change %',axis =1, inplace=True)
df_cities

City       State  Pop 2019 Est  Pop 2010  2016 Land SqMi  \
0    New York City    New York       8336817   8175133           301.5   
1      Los Angeles  California       3979576   3792621           468.7   
2          Chicago    Illinois       2693976   2695598           227.3   
3          Houston       Texas       2320268   2100263           637.5   
4          Phoenix     Arizona       1680992   1445632           517.6   
..             ...         ...           ...       ...             ...   
311     San Angelo       Texas        101004     93200            59.9   
312      Vacaville  California        100670     92428            29.0   
313        Clinton    Michigan        100471     96796            28.1   
314           Bend      Oregon        100421     76639            33.1   
315     Woodbridge  New Jersey        100145     99585            23.3   

     Density 2010  Density 2019 Est  Pop Change Prop.  
0    27114.868988      27651.134328            0.0198  
1     8091.787924       8490.667805            0.0493  
2    11859.208095      11852.072151           -0.0006  
3     3294.530196       3639.636078            0.1048  
4     2792.952087       3247.666151            0.1628  
..            ...               ...               ...  
311   1555.926544       1686.210351            0.0837  
312   3187.172414       3471.379310            0.0892  
313   3444.697509       3575.480427            0.0380  
314   2315.377644       3033.867069            0.3103  
315   4274.034335       4298.068670            0.0056  

[316 rows x 8 columns]

The dataframe above is now ready to use! We are now able to start filtering the cities to identify a subset that is similar to Dayton, Ohio in terms of population and land square miles to Dayton. But first, let's look at how the data is distributed. The df.describe method will be used to generate summary statistics for a quick review, while pandas profiling will be used to generate an interactive HTML report with plots and extremely detailed statistics.

In [16]:
df_cities.describe()

Pop 2019 Est      Pop 2010  2016 Land SqMi  Density 2010  \
count  3.160000e+02  3.160000e+02      316.000000    316.000000   
mean   3.017672e+05  2.785130e+05       93.162025   3928.887751   
std    5.821910e+05  5.612240e+05      135.408058   3182.517907   
min    1.001450e+05  7.509200e+04        6.400000    170.998477   
25%    1.189330e+05  1.096460e+05       33.925000   2048.137663   
50%    1.600280e+05  1.514075e+05       55.150000   3074.800247   
75%    2.621790e+05  2.366672e+05      103.875000   4468.330366   
max    8.336817e+06  8.175133e+06     1706.600000  27114.868988   

       Density 2019 Est  Pop Change Prop.  
count        316.000000        316.000000  
mean        4231.248248          0.097411  
std         3294.332220          0.104984  
min          168.756592         -0.074300  
25%         2303.383450          0.026225  
50%         3473.931034          0.082650  
75%         4818.254502          0.135025  
max        27651.134328          0.713800

In [17]:
cities_profile = ProfileReport(df_cities, title="Cities Profiling Report", samples=None, missing_diagrams=None, duplicates=None)
cities_profile.to_notebook_iframe()

Reviewing these statistics, a few bits of information stand out as noteworthy:
1. Among the 316 cities, the mean estimated population growth rate is **9.74%**, with the median at **8.26%**.
2. The bottom **25%** of the cities listed had a population growth rate under **2.62%**. The top **25%** of the cities listed had population growth above **13.5%**. 
3. California, Texas, Florida, Colorado, and Arizona contain **50.3%** of the cities listed.
4. The correlation between population growth and land square miles is surprisingly weak, only very slightly positive.
5. Similar to point 4, there is a weak negative correlation between 2010 population density and population growth.
6. While the relationships in points 4 and 5 are weak, they do suggest that cities with larger initial land areas and lower initial population densities are able to grow their populations faster. Intuitively, this makes sense - **cities that grew faster had more geographical room for population growth.**

We should now filter the dataframe for a list of cities that is similar to Dayton, Ohio in terms of population and land square miles. We'll use the 2010 population data to establish similarity -- using a 2010 baseline will help later on with inferring causal relationships between employer compositions and population growth.

Let's start by calling Dayton's population and land statistics:

In [18]:
df_dayton = df_cities[(df_cities['City'] == 'Dayton') & (df_cities['State'] == 'Ohio')]
df_dayton

City State  Pop 2019 Est  Pop 2010  2016 Land SqMi  Density 2010  \
194  Dayton  Ohio        140407    141527            55.7   2540.879713   

     Density 2019 Est  Pop Change Prop.  
194       2520.771993           -0.0079

We see above that Dayton's 2010 population was 141,527 people, and that land area for the city was around 55.7 square miles.
Let's filter the cities data frame sequentially for cities that are within +/- 20% of those numbers.

In [353]:
df_cities_filtered = df_cities[(df_cities['Pop 2010'].between(141527*0.8,141527*1.2))]
df_cities_filtered = df_cities_filtered[(df_cities_filtered['2016 Land SqMi'].between(55.7*0.8,55.7*1.2))]
df_cities_filtered.sort_values('Pop Change Prop.', ascending = False, inplace = True) # Sorting by Population Change Prop
df_cities_filtered.reset_index(drop=True, inplace = True)
df_cities_filtered

City           State  Pop 2019 Est  Pop 2010  2016 Land SqMi  \
0        McKinney           Texas        199177    131117            63.0   
1            Cary  North Carolina        170282    135234            56.5   
2         Killeen           Texas        151666    127921            53.5   
3    Fort Collins        Colorado        170243    143986            55.8   
4       Vancouver      Washington        184463    161791            46.9   
5         Ontario      California        185010    163924            49.9   
6           Salem          Oregon        174365    154637            48.6   
7          Olathe          Kansas        140545    125872            60.9   
8         Hayward      California        159203    144186            45.5   
9         McAllen           Texas        143268    129877            58.4   
10    Gainesville         Florida        133997    124354            62.3   
11      Lafayette       Louisiana        126185    120623            53.8   
12       Mesquite           Texas        140937    139824            47.2   
13     Evansville         Indiana        117979    117429            47.3   
14  Thousand Oaks      California        126813    126683            55.2   
15         Joliet        Illinois        147344    147433            64.4   
16         Dayton            Ohio        140407    141527            55.7   
17         Topeka          Kansas        125310    127473            61.5   
18    Springfield        Illinois        114230    116250            60.1   
19        Hampton        Virginia        134510    137436            51.5   
20         Peoria        Illinois        110417    115007            48.2   
21       Rockford        Illinois        145609    152871            63.5   

    Density 2010  Density 2019 Est  Pop Change Prop.  
0    2081.222222       3161.539683            0.5191  
1    2393.522124       3013.840708            0.2592  
2    2391.046729       2834.878505            0.1856  
3    2580.394265       3050.949821            0.1824  
4    3449.701493       3933.113006            0.1401  
5    3285.050100       3707.615230            0.1286  
6    3181.831276       3587.757202            0.1276  
7    2066.863711       2307.799672            0.1166  
8    3168.923077       3498.967033            0.1042  
9    2223.921233       2453.219178            0.1031  
10   1996.051364       2150.834671            0.0775  
11   2242.063197       2345.446097            0.0461  
12   2962.372881       2985.953390            0.0080  
13   2482.642706       2494.270613            0.0047  
14   2294.981884       2297.336957            0.0010  
15   2289.332298       2287.950311           -0.0006  
16   2540.879713       2520.771993           -0.0079  
17   2072.731707       2037.560976           -0.0170  
18   1934.276206       1900.665557           -0.0174  
19   2668.660194       2611.844660           -0.0213  
20   2386.037344       2290.809129           -0.0399  
21   2407.417323       2293.055118           -0.0475

In [20]:
df_cities_filtered.describe()

Pop 2019 Est       Pop 2010  2016 Land SqMi  Density 2010  \
count      22.000000      22.000000       22.000000     22.000000   
mean   147361.818182  135702.500000       54.986364   2504.541957   
std     24493.156095   14343.899091        6.176322    440.469695   
min    110417.000000  115007.000000       45.500000   1934.276206   
25%    128609.000000  126074.750000       48.925000   2228.456724   
50%    142102.500000  133175.500000       55.450000   2392.284426   
75%    167483.000000  144136.000000       60.700000   2646.593712   
max    199177.000000  163924.000000       64.400000   3449.701493   

       Density 2019 Est  Pop Change Prop.  
count         22.000000         22.000000  
mean        2716.644523          0.084191  
std          575.608206          0.128940  
min         1900.665557         -0.047500  
25%         2294.125578         -0.006075  
50%         2507.521303          0.061800  
75%         3041.672543          0.128350  
max         3933.113006          0.519100

It's notable that even though these cities were similar in size, they've exhibited a wide spread in population change since 2010, with a maximum of **51.91%** (McKinney, TX) and minimum of **-4.75%** (Rockford, IL). Dayton is near the bottom of this list, with a population change of **-0.79%**.

We will now start exporting census data for the above cities from US Census QuickFacts. The QuickFacts website limits comparison tables to a maximum of 6 cities, but multiple CSV exports can be easily combined and cleaned within MS Excel. Data science purists may object to using Excel instead of Python-based cleaning code, but it would have taken *way* too long to clean and consolidate all of the data points otherwise - each census record has over 60 dimensions to consider.

After I merged, cleaned, and transformed the data within Excel, I uploaded it to my GitHub repository. The code below imports the Excel file into a new QuickFacts dataframe, sets the Index column as the dataframe index (same numbering as the prior cities dataframe) then provides a .info report.

In [21]:
quickfacts_export_url = r'https://github.com/CMDavis1986/Coursera_Capstone/blob/main/QuickFacts%20Exports%20-%20Merged%20and%20Cleaned.xlsx?raw=true'
quickfacts_download = requests.get(quickfacts_export_url).content
df_quickfacts = pd.read_excel(quickfacts_download, sheet_name = 'Transformed')
df_quickfacts.set_index('Index',inplace=True)
df_quickfacts.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 21 entries, 0 to 21
Data columns (total 55 columns):
 #   Column                                                                               Non-Null Count  Dtype  
---  ------                                                                               --------------  -----  
 0   City                                                                                 21 non-null     object 
 1   State                                                                                21 non-null     object 
 2   Pop 2019 Est                                                                         21 non-null     int64  
 3   Pop 2010                                                                             21 non-null     int64  
 4   Pop Change Prop.                                                                     21 non-null     float64
 5   Persons under 5 years Prop.                                                          21 non-nu

Reviewing the report above, we see that two of the cities listed have null values for column 40, 'Total merchant wholesaler sales...". In case this is a useful datapoint, I'm going to leave it untouched while performing exploratory analysis.

Using the QuickFacts data, let's find out how well each city census measure correlates with population growth.

In [22]:
df_quickfacts_corr=df_quickfacts.corr() # Generating a dataframe that finds correlation coefficients between columns.
df_quickfacts_corr.sort_values('Pop Change Prop.',ascending = False, inplace = True) # Sorting
df_quickfacts_corr['Pop Change Prop.'] # Filtering the correlation dataframe for values in the Pop Change Prop. column.

Pop Change Prop.                                                                       1.000000
Pop 2019 Est                                                                           0.774475
Households with a computer Prop., 2014-2018                                            0.708578
Households with a broadband Internet subscription Prop., 2014-2018                     0.608455
Median household income (in 2018 dollars), 2014-2018                                   0.503509
Median selected monthly owner costs -without a mortgage, 2014-2018                     0.502873
In civilian labor force, total Prop. of population age 16 years+, 2014-2018            0.497406
Bachelor's degree or higher Prop. of persons age 25 years+, 2014-2018                  0.424968
Persons per household, 2014-2018                                                       0.394489
Median selected monthly owner costs -with a mortgage, 2014-2018                        0.383676
Mean travel time to work (minutes), work

**Fascinating!** The above list is a goldmine of useful statistics. Here are some highlights:

Fairly strong positive correlations:
1. The proportions of households with both a computer and broadband internet.
2. The median household income.
3. The proportion of people in the civilian labor force.

Fairly strong negative correlations:
1. Total health care and social assistance receipts/revenue.
2. Proportion of persons age 65 years and over.
3. Proportion of persons with a disability **under** age 65 years.
4. Proportion of persons in poverty.

*It's important to note that many of these figures are for the years 2014-2018 - it's difficult to say whether they reflect an effect or cause of population growth.*

Now let's look at how Dayton compares on these specific measures.

In [23]:
# Summary stats
df_quickfacts_stats = df_quickfacts.describe()
stats_columns = ['Households with a computer Prop., 2014-2018','Households with a broadband Internet subscription Prop., 2014-2018','Median household income (in 2018 dollars), 2014-2018','In civilian labor force, total Prop. of population age 16 years+, 2014-2018','Total health care and social assistance receipts/revenue, 2012 ($1,000)','Persons 65 years and over Prop.','With a disability, under age 65 years Prop., 2014-2018','Persons in poverty Prop.']
df_quickfacts_stats[stats_columns]

Households with a computer Prop., 2014-2018  \
count                                    21.000000   
mean                                      0.902762   
std                                       0.045606   
min                                       0.814000   
25%                                       0.868000   
50%                                       0.904000   
75%                                       0.936000   
max                                       0.974000   

       Households with a broadband Internet subscription Prop., 2014-2018  \
count                                          21.000000                    
mean                                            0.822381                    
std                                             0.070932                    
min                                             0.692000                    
25%                                             0.768000                    
50%                                             0.832000                    
75%                                             0.876000                    
max                                             0.940000                    

       Median household income (in 2018 dollars), 2014-2018  \
count                                          21.000000      
mean                                        60408.047619      
std                                         20737.844489      
min                                         31395.000000      
25%                                         47279.000000      
50%                                         53619.000000      
75%                                         67504.000000      
max                                        105485.000000      

       In civilian labor force, total Prop. of population age 16 years+, 2014-2018  \
count                                          21.000000                             
mean                                            0.644571                             
std                                             0.046610                             
min                                             0.569000                             
25%                                             0.615000                             
50%                                             0.625000                             
75%                                             0.676000                             
max                                             0.742000                             

       Total health care and social assistance receipts/revenue, 2012 ($1,000)  \
count                                       2.100000e+01                         
mean                                        1.494317e+06                         
std                                         7.716042e+05                         
min                                         1.812340e+05                         
25%                                         8.886680e+05                         
50%                                         1.447571e+06                         
75%                                         2.178927e+06                         
max                                         3.059522e+06                         

       Persons 65 years and over Prop.  \
count                        21.000000   
mean                          0.129095   
std                           0.031810   
min                           0.059000   
25%                           0.103000   
50%                           0.128000   
75%                           0.153000   
max                           0.183000   

       With a disability, under age 65 years Prop., 2014-2018  \
count                                          21.000000        
mean                                            0.086476        
std                                             0.030625        
min                                             0.040000        
25%                                     

In [24]:
# Stats for Dayton:
df_quickfacts_dayton = df_quickfacts[(df_quickfacts['City'] == 'Dayton') & (df_quickfacts['State'] == 'Ohio')]
df_quickfacts_dayton[stats_columns]

Households with a computer Prop., 2014-2018  \
Index                                                
16                                           0.814   

       Households with a broadband Internet subscription Prop., 2014-2018  \
Index                                                                       
16                                                  0.73                    

       Median household income (in 2018 dollars), 2014-2018  \
Index                                                         
16                                                 31395      

       In civilian labor force, total Prop. of population age 16 years+, 2014-2018  \
Index                                                                                
16                                                 0.569                             

       Total health care and social assistance receipts/revenue, 2012 ($1,000)  \
Index                                                                            
16                                               3059522                         

       Persons 65 years and over Prop.  \
Index                                    
16                               0.124   

       With a disability, under age 65 years Prop., 2014-2018  \
Index                                                           
16                                                 0.142        

       Persons in poverty Prop.  
Index                            
16                        0.321

Reviewing the two tables above, we observe the following:
1. Of the cities in the QuickFact set, Dayton has the lowest values for household computer ownership, civilian labor force participation, and median household income.
2. Dayton has the highest values for healthcare/social assistance receipts/revenue, population disabled under age 65, and poverty rate.
3. Dayton is surprisingly middle-of-the road on the proportion of population age 65 and over. This neither helps nor hurts population growth.

It's pretty easy to see that Dayton is underperforming on several measures here.
The economic picture is not pretty -- the data suggests that Dayton does not have enough **jobs**, let alone **high-paying jobs**, to support population growth. Furthermore, a larger proportion of the under-65 population is encumbered with disabilities and higher medical expenses. Computer and internet access is lower, which could reflect both demand-side and supply-side issues.

Now let's see how Dayton's employer portfolio compares to the other cities. We will use the Foursquare API to collect location data for employers in each city.

### Comparing Employer Portfolios - Dayton, Ohio vs. 21 Similarly-Sized Cities

To begin using Foursquare's API, I will need a list of geographical coordinates specific to individual zip codes from each city. I will also need to specify a search radius around each coordinate.

We must ask an important question though - **how can we avoid biases in the location data?** 

For example - how do we know that the search radius is appropriate for a particular geographical coordinate? If the radius is too big, the search results may accidentally include results from adjacent zip codes, causing duplicates in the city aggregate results. If the radius is too small, the search results could be biased by the particular type of zoning in the area around the coordinate -- a coordinate in an industrial zone will likely have a lot of factories, but this may not be representative of the zip code as a whole. Furthermore, zip codes are often irregularly-shaped, which makes setting an appropriate search radius that much more difficult.

Another question to consider is the effect of surrounding metropolitan areas. In many cities (Dayton included) zip code areas have sections that are both inside and outside of city boundaries. This makes it very difficult to assign a proper weight to the results, as the % of population and businesses inside and outside of the city boundaries may not be known.

Another source of bias is Foursquare's recommendation algorithm. Foursquare's search results tend to prioritize food and entertainment venues, which could skew the results and paint an inaccurate picture of a locality's employer portfolio. We could potentially work around this by collecting a larger list of businesses using Foursquare's explore endpoint.

**Attempting to correctly address all of these potential biases is well outside the scope of this project.** However, [simplemaps.com](https://simplemaps.com/data/us-zips) provides a useful zip code database that contains population numbers and densities - we can use this information to calculate the square miles within each zip code. From the area, we can then calculate a search radius. Later on, we can weight the search results by the proportion of total population within that zip code.

Once again, I have opted to clean the database (and also calculate radius and population proportions) within Excel, rather than waste time attempting to script the cleaning process in Python. Sorry data science / Python purists!

In [25]:
# Importing my GitHub zip code Excel file to a dataframe.
zips_export_url = r'https://github.com/CMDavis1986/Coursera_Capstone/blob/main/uszips%20-Cleaned.xlsx?raw=true'
zips_download = requests.get(zips_export_url).content
df_zips = pd.read_excel(zips_download, sheet_name = 'Cleaned')
df_zips.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 156 entries, 0 to 155
Data columns (total 11 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   City_Index  156 non-null    int64  
 1   City        156 non-null    object 
 2   State       156 non-null    object 
 3   ZIP         156 non-null    int64  
 4   lat         156 non-null    float64
 5   lng         156 non-null    float64
 6   Population  156 non-null    int64  
 7   Density     156 non-null    float64
 8   Zip SqMi    156 non-null    float64
 9   Radius Mi   156 non-null    float64
 10  Radius m    156 non-null    float64
dtypes: float64(6), int64(3), object(2)
memory usage: 13.5+ KB


In [26]:
df_zips.head()

City_Index      City           State    ZIP       lat       lng  \
0           0  McKinney           Texas  75069  33.16547 -96.59469   
1           0  McKinney           Texas  75070  33.17311 -96.69773   
2           0  McKinney           Texas  75071  33.24664 -96.62898   
3           1      Cary  North Carolina  27511  35.76326 -78.78432   
4           1      Cary  North Carolina  27513  35.80223 -78.80270   

   Population  Density    Zip SqMi  Radius Mi      Radius m  
0       37834    411.4   91.964025   5.410458   8707.266872  
1       98219   1208.3   81.286932   5.086692   8186.216680  
2       52939    176.8  299.428733   9.762742  15711.570763  
3       34525   1055.3   32.715815   3.227037   5193.399646  
4       44821    995.7   45.014563   3.785311   6091.852604

In [29]:
# Setting Foursquare access variables:
CLIENT_ID = 'GL2MNJ1FWQWBX2FJLO5PCVUAJE531MHKYSUUUIJXMIBBNLR1' # your Foursquare ID
CLIENT_SECRET = 'M2KXZW0F5ZZSNINK4F0MVXJB0LEK5SVPWBBD0VCZKKPFYRCN' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

In [30]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [157]:
# Defining function for getting Nearby Venues
def getNearbyVenues(City_Index,
                    City,
                    State,
                    zipcode,
                    Population,
                    latitudes,
                    longitudes,
                    search_radius,
                    category_id):
    
    venues_list=[]
    for City_Index, City, State, zipcode, Population, lat, lng, search_radius in zip(City_Index, City, State, zipcode, Population, latitudes, longitudes, search_radius):
        print(zipcode)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&categoryId={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            search_radius,
            category_id,
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(City_Index,
                             City,
                             State,
                             zipcode,
                             Population, 
                             lat,
                             lng,
                             v['venue']['name'],
                             v['venue']['location']['formattedAddress'],
                             v['venue']['location']['lat'],
                             v['venue']['location']['lng'],
                             v['venue']['categories'][0]['name'],
                             category_id) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['City_Index','City','State','ZIP','ZIP Population','ZIP Latitude','ZIP Longitude','Venue','Venue Address','Venue Latitude','Venue Longitude','Venue Category','Category ID']
    
    return(nearby_venues)

In the cells below, we are going to sequentially run location data queries for each of Foursquare's top-level venue categories, which include the following:
1. Arts & Entertainment
2. College & University
3. Event 
4. Food 
5. Nightlife Spot
6. Outdoors & Recreation
7. Residence 
8. Shop & Service
9. Travel & Transport
10. Professional & Other Places

The query results data will be stored in unique dataframes for each top-level venue category.

In [158]:
# Creating dataframe for nearby Arts & Entertainment venues in each zip code:
df_arts_entertainment = getNearbyVenues(City_Index=df_zips['City_Index'],
                                        City=df_zips['City'],
                                        State=df_zips['State'],
                                        zipcode=df_zips['ZIP'],
                                        Population=df_zips['Population'],
                                        latitudes=df_zips['lat'],
                                        longitudes=df_zips['lng'],
                                        search_radius=df_zips['Radius m'],
                                        category_id='4d4b7104d754a06370d81259') # Arts & Entertainment
df_arts_entertainment.head()

75069
75070
75071
27511
27513
27518
27519
76541
76542
76543
76549
80521
80524
80525
80526
80528
98660
98661
98662
98663
98664
98665
98682
98683
98684
98685
98686
91761
91762
91764
97301
97302
97303
97304
97305
97306
97317
66061
66062
94541
94542
94544
94545
78501
78503
78504
32601
32603
32605
32606
32607
32608
32609
32612
32641
32653
70501
70503
70506
70507
70508
75149
75150
75181
47708
47710
47711
47712
47713
47714
47715
47720
47725
91360
91362
60431
60432
60433
60435
60436
45402
45403
45404
45405
45406
45409
45410
45414
45415
45416
45417
45419
45420
45424
45426
45428
45429
45430
45431
45432
45433
45434
45439
45440
45449
45458
45459
66603
66604
66605
66606
66607
66608
66609
66610
66611
66612
66614
66615
66616
66617
66618
66619
66621
66622
62701
62702
62703
62704
62707
62711
62712
23661
23663
23664
23665
23666
23669
61602
61603
61604
61605
61606
61607
61614
61615
61625
61101
61102
61103
61104
61107
61108
61109
61112
61114


City_Index      City  State    ZIP  ZIP Population  ZIP Latitude  \
0           0  McKinney  Texas  75069           37834      33.16547   
1           0  McKinney  Texas  75069           37834      33.16547   
2           0  McKinney  Texas  75069           37834      33.16547   
3           0  McKinney  Texas  75069           37834      33.16547   
4           0  McKinney  Texas  75069           37834      33.16547   

   ZIP Longitude                            Venue  \
0      -96.59469  McKinney Performing Arts Center   
1      -96.59469           iPic Theaters Fairview   
2      -96.59469               Allen Event Center   
3      -96.59469                         Cinemark   
4      -96.59469                         Cinemark   

                                       Venue Address  Venue Latitude  \
0  [111 N Tennessee St (btwn W Virginia & W Louis...       33.197630   
1   [321 Town Pl, Fairview, TX 75069, United States]       33.132561   
2  [200 E Stacy Rd (at Hwy 75), Allen, TX 75002, ...       33.127451   
3  [921 SH 121 (at N. Watters Dr.), Allen, TX 750...       33.144281   
4  [1701 S Central Expy (at Parkview Ave), McKinn...       33.187873   

   Venue Longitude Venue Category               Category ID  
0       -96.615563        Theater  4d4b7104d754a06370d81259  
1       -96.647687  Movie Theater  4d4b7104d754a06370d81259  
2       -96.654616    Music Venue  4d4b7104d754a06370d81259  
3       -96.673905  Movie Theater  4d4b7104d754a06370d81259  
4       -96.637661  Movie Theater  4d4b7104d754a06370d81259

In [160]:
# Creating dataframe for nearby College & University venues in each zip code:
df_college_university = getNearbyVenues(City_Index=df_zips['City_Index'],
                                        City=df_zips['City'],
                                        State=df_zips['State'],
                                        zipcode=df_zips['ZIP'],
                                        Population=df_zips['Population'],
                                        latitudes=df_zips['lat'],
                                        longitudes=df_zips['lng'],
                                        search_radius=df_zips['Radius m'],
                            category_id='4d4b7105d754a06372d81259') # College & University
df_college_university.head()

75069
75070
75071
27511
27513
27518
27519
76541
76542
76543
76549
80521
80524
80525
80526
80528
98660
98661
98662
98663
98664
98665
98682
98683
98684
98685
98686
91761
91762
91764
97301
97302
97303
97304
97305
97306
97317
66061
66062
94541
94542
94544
94545
78501
78503
78504
32601
32603
32605
32606
32607
32608
32609
32612
32641
32653
70501
70503
70506
70507
70508
75149
75150
75181
47708
47710
47711
47712
47713
47714
47715
47720
47725
91360
91362
60431
60432
60433
60435
60436
45402
45403
45404
45405
45406
45409
45410
45414
45415
45416
45417
45419
45420
45424
45426
45428
45429
45430
45431
45432
45433
45434
45439
45440
45449
45458
45459
66603
66604
66605
66606
66607
66608
66609
66610
66611
66612
66614
66615
66616
66617
66618
66619
66621
66622
62701
62702
62703
62704
62707
62711
62712
23661
23663
23664
23665
23666
23669
61602
61603
61604
61605
61606
61607
61614
61615
61625
61101
61102
61103
61104
61107
61108
61109
61112
61114


City_Index      City  State    ZIP  ZIP Population  ZIP Latitude  \
0           0  McKinney  Texas  75069           37834      33.16547   
1           0  McKinney  Texas  75069           37834      33.16547   
2           0  McKinney  Texas  75069           37834      33.16547   
3           0  McKinney  Texas  75069           37834      33.16547   
4           0  McKinney  Texas  75069           37834      33.16547   

   ZIP Longitude                                              Venue  \
0      -96.59469  University of North Texas at the Collin Higher...   
1      -96.59469                     Texas A&M Commerce in McKinney   
2      -96.59469                                Citychurch McKinney   
3      -96.59469                           Heritage Learning Center   
4      -96.59469                    Collin College CPC Computer Lab   

                                       Venue Address  Venue Latitude  \
0  [3452 Spur 399, McKinney, TX 75069, United Sta...       33.162319   
1                          [TX 75069, United States]       33.162376   
2  [320 Industrial Blvd Ste 202, McKinney, TX 750...       33.177945   
3  [200 Jordan Rd (Virginia), McKinney, TX 75070,...       33.199828   
4                [McKinney, TX 75071, United States]       33.218247   

   Venue Longitude             Venue Category               Category ID  
0       -96.638963  College Academic Building  4d4b7105d754a06372d81259  
1       -96.639012          College Classroom  4d4b7105d754a06372d81259  
2       -96.608463             Student Center  4d4b7105d754a06372d81259  
3       -96.654470          College Classroom  4d4b7105d754a06372d81259  
4       -96.641548          College Classroom  4d4b7105d754a06372d81259

In [161]:
# Creating dataframe for nearby Event venues in each zip code:
df_event = getNearbyVenues(City_Index=df_zips['City_Index'],
                                        City=df_zips['City'],
                                        State=df_zips['State'],
                                        zipcode=df_zips['ZIP'],
                                        Population=df_zips['Population'],
                                        latitudes=df_zips['lat'],
                                        longitudes=df_zips['lng'],
                                        search_radius=df_zips['Radius m'],
                            category_id='4d4b7105d754a06373d81259') # Event
df_event.head()

75069
75070
75071
27511
27513
27518
27519
76541
76542
76543
76549
80521
80524
80525
80526
80528
98660
98661
98662
98663
98664
98665
98682
98683
98684
98685
98686
91761
91762
91764
97301
97302
97303
97304
97305
97306
97317
66061
66062
94541
94542
94544
94545
78501
78503
78504
32601
32603
32605
32606
32607
32608
32609
32612
32641
32653
70501
70503
70506
70507
70508
75149
75150
75181
47708
47710
47711
47712
47713
47714
47715
47720
47725
91360
91362
60431
60432
60433
60435
60436
45402
45403
45404
45405
45406
45409
45410
45414
45415
45416
45417
45419
45420
45424
45426
45428
45429
45430
45431
45432
45433
45434
45439
45440
45449
45458
45459
66603
66604
66605
66606
66607
66608
66609
66610
66611
66612
66614
66615
66616
66617
66618
66619
66621
66622
62701
62702
62703
62704
62707
62711
62712
23661
23663
23664
23665
23666
23669
61602
61603
61604
61605
61606
61607
61614
61615
61625
61101
61102
61103
61104
61107
61108
61109
61112
61114


City_Index      City  State    ZIP  ZIP Population  ZIP Latitude  \
0           0  McKinney  Texas  75069           37834      33.16547   
1           0  McKinney  Texas  75069           37834      33.16547   
2           0  McKinney  Texas  75070           98219      33.17311   
3           0  McKinney  Texas  75070           98219      33.17311   
4           0  McKinney  Texas  75071           52939      33.24664   

   ZIP Longitude                        Venue  \
0      -96.59469  McKinney ISD Holiday Bazaar   
1      -96.59469  Clearwater Beach Waterslide   
2      -96.69773                    Kidstrong   
3      -96.69773  McKinney ISD Holiday Bazaar   
4      -96.62898  McKinney ISD Holiday Bazaar   

                                       Venue Address  Venue Latitude  \
0  [1400 Wilson Creek Pkwy (S. Graves Street), Mc...       33.187996   
1  [1 Causeway Blvd (pier 60), Clearwater, FL 337...       33.187308   
2  [7810 Eldorado Pkwy, McKinney, TX 75070, Unite...       33.174847   
3  [1400 Wilson Creek Pkwy (S. Graves Street), Mc...       33.187996   
4  [1400 Wilson Creek Pkwy (S. Graves Street), Mc...       33.187996   

   Venue Longitude         Venue Category               Category ID  
0       -96.632240       Christmas Market  4d4b7105d754a06373d81259  
1       -96.542358  General Entertainment  4d4b7105d754a06373d81259  
2       -96.719536       Indoor Play Area  4d4b7105d754a06373d81259  
3       -96.632240       Christmas Market  4d4b7105d754a06373d81259  
4       -96.632240       Christmas Market  4d4b7105d754a06373d81259

In [162]:
# Creating dataframe for nearby Food venues in each zip code:
df_food = getNearbyVenues(City_Index=df_zips['City_Index'],
                                        City=df_zips['City'],
                                        State=df_zips['State'],
                                        zipcode=df_zips['ZIP'],
                                        Population=df_zips['Population'],
                                        latitudes=df_zips['lat'],
                                        longitudes=df_zips['lng'],
                                        search_radius=df_zips['Radius m'],
                            category_id='4d4b7105d754a06374d81259') # Food
df_food.head()

75069
75070
75071
27511
27513
27518
27519
76541
76542
76543
76549
80521
80524
80525
80526
80528
98660
98661
98662
98663
98664
98665
98682
98683
98684
98685
98686
91761
91762
91764
97301
97302
97303
97304
97305
97306
97317
66061
66062
94541
94542
94544
94545
78501
78503
78504
32601
32603
32605
32606
32607
32608
32609
32612
32641
32653
70501
70503
70506
70507
70508
75149
75150
75181
47708
47710
47711
47712
47713
47714
47715
47720
47725
91360
91362
60431
60432
60433
60435
60436
45402
45403
45404
45405
45406
45409
45410
45414
45415
45416
45417
45419
45420
45424
45426
45428
45429
45430
45431
45432
45433
45434
45439
45440
45449
45458
45459
66603
66604
66605
66606
66607
66608
66609
66610
66611
66612
66614
66615
66616
66617
66618
66619
66621
66622
62701
62702
62703
62704
62707
62711
62712
23661
23663
23664
23665
23666
23669
61602
61603
61604
61605
61606
61607
61614
61615
61625
61101
61102
61103
61104
61107
61108
61109
61112
61114


City_Index      City  State    ZIP  ZIP Population  ZIP Latitude  \
0           0  McKinney  Texas  75069           37834      33.16547   
1           0  McKinney  Texas  75069           37834      33.16547   
2           0  McKinney  Texas  75069           37834      33.16547   
3           0  McKinney  Texas  75069           37834      33.16547   
4           0  McKinney  Texas  75069           37834      33.16547   

   ZIP Longitude               Venue  \
0      -96.59469        Patina Green   
1      -96.59469       Square Burger   
2      -96.59469    Thai Noodle Wave   
3      -96.59469  Cadillac Pizza Pub   
4      -96.59469     Texas Roadhouse   

                                       Venue Address  Venue Latitude  \
0                [McKinney, TX 75069, United States]       33.197868   
1  [115 N Kentucky St (at W Virginia St), McKinne...       33.197828   
2  [2775 S Central Expy Ste 180, McKinney, TX 750...       33.174603   
3  [112 S Kentucky St, McKinney, TX 75069, United...       33.196823   
4  [3101 S. Central Expressway, McKinney, TX 7507...       33.170045   

   Venue Longitude   Venue Category               Category ID  
0       -96.614964             Café  4d4b7105d754a06374d81259  
1       -96.615880     Burger Joint  4d4b7105d754a06374d81259  
2       -96.639032  Thai Restaurant  4d4b7105d754a06374d81259  
3       -96.615977      Pizza Place  4d4b7105d754a06374d81259  
4       -96.640000       Steakhouse  4d4b7105d754a06374d81259

In [159]:
# Creating dataframe for nearby Nightlife Spot venues in each zip code:
df_nightlife = getNearbyVenues(City_Index=df_zips['City_Index'],
                               City=df_zips['City'],
                               State=df_zips['State'],
                               zipcode=df_zips['ZIP'],
                               Population=df_zips['Population'],
                               latitudes=df_zips['lat'],
                               longitudes=df_zips['lng'],
                               search_radius=df_zips['Radius m'],
                               category_id='4d4b7105d754a06376d81259') # Nightlife Spot
df_nightlife.head()

75069
75070
75071
27511
27513
27518
27519
76541
76542
76543
76549
80521
80524
80525
80526
80528
98660
98661
98662
98663
98664
98665
98682
98683
98684
98685
98686
91761
91762
91764
97301
97302
97303
97304
97305
97306
97317
66061
66062
94541
94542
94544
94545
78501
78503
78504
32601
32603
32605
32606
32607
32608
32609
32612
32641
32653
70501
70503
70506
70507
70508
75149
75150
75181
47708
47710
47711
47712
47713
47714
47715
47720
47725
91360
91362
60431
60432
60433
60435
60436
45402
45403
45404
45405
45406
45409
45410
45414
45415
45416
45417
45419
45420
45424
45426
45428
45429
45430
45431
45432
45433
45434
45439
45440
45449
45458
45459
66603
66604
66605
66606
66607
66608
66609
66610
66611
66612
66614
66615
66616
66617
66618
66619
66621
66622
62701
62702
62703
62704
62707
62711
62712
23661
23663
23664
23665
23666
23669
61602
61603
61604
61605
61606
61607
61614
61615
61625
61101
61102
61103
61104
61107
61108
61109
61112
61114


City_Index      City  State    ZIP  ZIP Population  ZIP Latitude  \
0           0  McKinney  Texas  75069           37834      33.16547   
1           0  McKinney  Texas  75069           37834      33.16547   
2           0  McKinney  Texas  75069           37834      33.16547   
3           0  McKinney  Texas  75069           37834      33.16547   
4           0  McKinney  Texas  75069           37834      33.16547   

   ZIP Longitude                   Venue  \
0      -96.59469           Tupps Brewery   
1      -96.59469           Square Burger   
2      -96.59469      Cadillac Pizza Pub   
3      -96.59469  iPic Theaters Fairview   
4      -96.59469           Landon Winery   

                                       Venue Address  Venue Latitude  \
0  [721 Anderson St, McKinney, TX 75069, United S...       33.183863   
1  [115 N Kentucky St (at W Virginia St), McKinne...       33.197828   
2  [112 S Kentucky St, McKinney, TX 75069, United...       33.196823   
3   [321 Town Pl, Fairview, TX 75069, United States]       33.132561   
4  [101 N Kentucky St (Louisiana), McKinney, TX 7...       33.197321   

   Venue Longitude Venue Category               Category ID  
0       -96.610180        Brewery  4d4b7105d754a06376d81259  
1       -96.615880   Burger Joint  4d4b7105d754a06376d81259  
2       -96.615977    Pizza Place  4d4b7105d754a06376d81259  
3       -96.647687  Movie Theater  4d4b7105d754a06376d81259  
4       -96.615884       Wine Bar  4d4b7105d754a06376d81259

In [166]:
# Creating dataframe for nearby Outdoors & Recreation venues in each zip code:
df_outdoors_recreation = getNearbyVenues(City_Index=df_zips['City_Index'],
                               City=df_zips['City'],
                               State=df_zips['State'],
                               zipcode=df_zips['ZIP'],
                               Population=df_zips['Population'],
                               latitudes=df_zips['lat'],
                               longitudes=df_zips['lng'],
                               search_radius=df_zips['Radius m'],
                            category_id='4d4b7105d754a06377d81259') # Outdoors & Recreation
df_outdoors_recreation.head()

75069
75070
75071
27511
27513
27518
27519
76541
76542
76543
76549
80521
80524
80525
80526
80528
98660
98661
98662
98663
98664
98665
98682
98683
98684
98685
98686
91761
91762
91764
97301
97302
97303
97304
97305
97306
97317
66061
66062
94541
94542
94544
94545
78501
78503
78504
32601
32603
32605
32606
32607
32608
32609
32612
32641
32653
70501
70503
70506
70507
70508
75149
75150
75181
47708
47710
47711
47712
47713
47714
47715
47720
47725
91360
91362
60431
60432
60433
60435
60436
45402
45403
45404
45405
45406
45409
45410
45414
45415
45416
45417
45419
45420
45424
45426
45428
45429
45430
45431
45432
45433
45434
45439
45440
45449
45458
45459
66603
66604
66605
66606
66607
66608
66609
66610
66611
66612
66614
66615
66616
66617
66618
66619
66621
66622
62701
62702
62703
62704
62707
62711
62712
23661
23663
23664
23665
23666
23669
61602
61603
61604
61605
61606
61607
61614
61615
61625
61101
61102
61103
61104
61107
61108
61109
61112
61114


City_Index      City  State    ZIP  ZIP Population  ZIP Latitude  \
0           0  McKinney  Texas  75069           37834      33.16547   
1           0  McKinney  Texas  75069           37834      33.16547   
2           0  McKinney  Texas  75069           37834      33.16547   
3           0  McKinney  Texas  75069           37834      33.16547   
4           0  McKinney  Texas  75069           37834      33.16547   

   ZIP Longitude                                              Venue  \
0      -96.59469  Heard Natural Science Museum & Wildlife Sanctuary   
1      -96.59469                                        Cotton Mill   
2      -96.59469                                    Towne Lake Park   
3      -96.59469                              Eldorado Country Club   
4      -96.59469                                   Celebration Park   

                                       Venue Address  Venue Latitude  \
0   [1 Nature Pl, McKinney, TX 75069, United States]       33.158383   
1    [610 Elm St, McKinney, TX 75069, United States]       33.184935   
2                [McKinney, TX 75069, United States]       33.185286   
3  [2604 Country Club Dr, McKinney, TX 75070, Uni...       33.177133   
4   [701 Angel Pkwy, Allen, TX 75002, United States]       33.107432   

   Venue Longitude Venue Category               Category ID  
0       -96.615240          Trail  4d4b7105d754a06377d81259  
1       -96.611397         Garden  4d4b7105d754a06377d81259  
2       -96.633272           Park  4d4b7105d754a06377d81259  
3       -96.650427    Golf Course  4d4b7105d754a06377d81259  
4       -96.624155           Park  4d4b7105d754a06377d81259

In [163]:
# Creating dataframe for nearby Residence venues in each zip code:
df_residence = getNearbyVenues(City_Index=df_zips['City_Index'],
                               City=df_zips['City'],
                               State=df_zips['State'],
                               zipcode=df_zips['ZIP'],
                               Population=df_zips['Population'],
                               latitudes=df_zips['lat'],
                               longitudes=df_zips['lng'],
                               search_radius=df_zips['Radius m'],
                               category_id='4e67e38e036454776db1fb3a') # Residence
df_residence.head()

75069
75070
75071
27511
27513
27518
27519
76541
76542
76543
76549
80521
80524
80525
80526
80528
98660
98661
98662
98663
98664
98665
98682
98683
98684
98685
98686
91761
91762
91764
97301
97302
97303
97304
97305
97306
97317
66061
66062
94541
94542
94544
94545
78501
78503
78504
32601
32603
32605
32606
32607
32608
32609
32612
32641
32653
70501
70503
70506
70507
70508
75149
75150
75181
47708
47710
47711
47712
47713
47714
47715
47720
47725
91360
91362
60431
60432
60433
60435
60436
45402
45403
45404
45405
45406
45409
45410
45414
45415
45416
45417
45419
45420
45424
45426
45428
45429
45430
45431
45432
45433
45434
45439
45440
45449
45458
45459
66603
66604
66605
66606
66607
66608
66609
66610
66611
66612
66614
66615
66616
66617
66618
66619
66621
66622
62701
62702
62703
62704
62707
62711
62712
23661
23663
23664
23665
23666
23669
61602
61603
61604
61605
61606
61607
61614
61615
61625
61101
61102
61103
61104
61107
61108
61109
61112
61114


City_Index      City  State    ZIP  ZIP Population  ZIP Latitude  \
0           0  McKinney  Texas  75069           37834      33.16547   
1           0  McKinney  Texas  75069           37834      33.16547   
2           0  McKinney  Texas  75069           37834      33.16547   
3           0  McKinney  Texas  75069           37834      33.16547   
4           0  McKinney  Texas  75069           37834      33.16547   

   ZIP Longitude                                     Venue  \
0      -96.59469     Meridian at Southgate by Ashton Woods   
1      -96.59469  McKinney Village at the Medical District   
2      -96.59469         The Gables of McKinney Apartments   
3      -96.59469         Lakes of Eldorado Apartment Homes   
4      -96.59469                        Cliffs Of Eldorado   

                                       Venue Address  Venue Latitude  \
0  [3100 Taunton Way, McKinney, TX 75069, United ...       33.171122   
1  [201 McKinney Village Pkwy, McKinney, TX 75069...       33.161155   
2  [1500 W Eldorado Pkwy, McKinney, TX 75069, Uni...       33.174996   
3  [1400 Eldorado Pkwy, McKinney, TX 75069, Unite...       33.176304   
4                      [McKinney, TX, United States]       33.177717   

   Venue Longitude                            Venue Category  \
0       -96.630619  Residential Building (Apartment / Condo)   
1       -96.632352  Residential Building (Apartment / Condo)   
2       -96.637410  Residential Building (Apartment / Condo)   
3       -96.637760  Residential Building (Apartment / Condo)   
4       -96.637562  Residential Building (Apartment / Condo)   

                Category ID  
0  4e67e38e036454776db1fb3a  
1  4e67e38e036454776db1fb3a  
2  4e67e38e036454776db1fb3a  
3  4e67e38e036454776db1fb3a  
4  4e67e38e036454776db1fb3a

In [165]:
# Creating dataframe for nearby Shop & Service venues in each zip code:
df_shop_service = getNearbyVenues(City_Index=df_zips['City_Index'],
                               City=df_zips['City'],
                               State=df_zips['State'],
                               zipcode=df_zips['ZIP'],
                               Population=df_zips['Population'],
                               latitudes=df_zips['lat'],
                               longitudes=df_zips['lng'],
                               search_radius=df_zips['Radius m'],
                            category_id='4d4b7105d754a06378d81259') # Shop & Service
df_shop_service.head()

75069
75070
75071
27511
27513
27518
27519
76541
76542
76543
76549
80521
80524
80525
80526
80528
98660
98661
98662
98663
98664
98665
98682
98683
98684
98685
98686
91761
91762
91764
97301
97302
97303
97304
97305
97306
97317
66061
66062
94541
94542
94544
94545
78501
78503
78504
32601
32603
32605
32606
32607
32608
32609
32612
32641
32653
70501
70503
70506
70507
70508
75149
75150
75181
47708
47710
47711
47712
47713
47714
47715
47720
47725
91360
91362
60431
60432
60433
60435
60436
45402
45403
45404
45405
45406
45409
45410
45414
45415
45416
45417
45419
45420
45424
45426
45428
45429
45430
45431
45432
45433
45434
45439
45440
45449
45458
45459
66603
66604
66605
66606
66607
66608
66609
66610
66611
66612
66614
66615
66616
66617
66618
66619
66621
66622
62701
62702
62703
62704
62707
62711
62712
23661
23663
23664
23665
23666
23669
61602
61603
61604
61605
61606
61607
61614
61615
61625
61101
61102
61103
61104
61107
61108
61109
61112
61114


City_Index      City  State    ZIP  ZIP Population  ZIP Latitude  \
0           0  McKinney  Texas  75069           37834      33.16547   
1           0  McKinney  Texas  75069           37834      33.16547   
2           0  McKinney  Texas  75069           37834      33.16547   
3           0  McKinney  Texas  75069           37834      33.16547   
4           0  McKinney  Texas  75069           37834      33.16547   

   ZIP Longitude                       Venue  \
0      -96.59469                Trader Joe's   
1      -96.59469           Bed Bath & Beyond   
2      -96.59469  Local Yocal Farm-to-Market   
3      -96.59469            Half Price Books   
4      -96.59469                    QuikTrip   

                                       Venue Address  Venue Latitude  \
0  [2851 Craig Dr Ste 100, McKinney, TX 75070, Un...       33.173674   
1  [2975 Craig Dr (at Eldorado Pkwy), McKinney, T...       33.172710   
2  [213 N Tennessee St, McKinney, TX 75069, Unite...       33.198474   
3  [3190 S Central Expy, McKinney, TX 75070, Unit...       33.170361   
4  [1700 S McDonald St (at Eldorado Pkwy.), McKin...       33.179174   

   Venue Longitude          Venue Category               Category ID  
0       -96.642839           Grocery Store  4d4b7105d754a06378d81259  
1       -96.643298  Furniture / Home Store  4d4b7105d754a06378d81259  
2       -96.615130          Farmers Market  4d4b7105d754a06378d81259  
3       -96.642792               Bookstore  4d4b7105d754a06378d81259  
4       -96.619651       Convenience Store  4d4b7105d754a06378d81259

In [167]:
# Creating dataframe for nearby Travel & Transport venues in each zip code:
df_travel_transport = getNearbyVenues(City_Index=df_zips['City_Index'],
                               City=df_zips['City'],
                               State=df_zips['State'],
                               zipcode=df_zips['ZIP'],
                               Population=df_zips['Population'],
                               latitudes=df_zips['lat'],
                               longitudes=df_zips['lng'],
                               search_radius=df_zips['Radius m'],
                            category_id='4d4b7105d754a06379d81259') # Travel & Transport
df_travel_transport.head()

75069
75070
75071
27511
27513
27518
27519
76541
76542
76543
76549
80521
80524
80525
80526
80528
98660
98661
98662
98663
98664
98665
98682
98683
98684
98685
98686
91761
91762
91764
97301
97302
97303
97304
97305
97306
97317
66061
66062
94541
94542
94544
94545
78501
78503
78504
32601
32603
32605
32606
32607
32608
32609
32612
32641
32653
70501
70503
70506
70507
70508
75149
75150
75181
47708
47710
47711
47712
47713
47714
47715
47720
47725
91360
91362
60431
60432
60433
60435
60436
45402
45403
45404
45405
45406
45409
45410
45414
45415
45416
45417
45419
45420
45424
45426
45428
45429
45430
45431
45432
45433
45434
45439
45440
45449
45458
45459
66603
66604
66605
66606
66607
66608
66609
66610
66611
66612
66614
66615
66616
66617
66618
66619
66621
66622
62701
62702
62703
62704
62707
62711
62712
23661
23663
23664
23665
23666
23669
61602
61603
61604
61605
61606
61607
61614
61615
61625
61101
61102
61103
61104
61107
61108
61109
61112
61114


City_Index      City  State    ZIP  ZIP Population  ZIP Latitude  \
0           0  McKinney  Texas  75069           37834      33.16547   
1           0  McKinney  Texas  75069           37834      33.16547   
2           0  McKinney  Texas  75069           37834      33.16547   
3           0  McKinney  Texas  75069           37834      33.16547   
4           0  McKinney  Texas  75069           37834      33.16547   

   ZIP Longitude                                              Venue  \
0      -96.59469               Collin County Regional Airport (TKI)   
1      -96.59469                            Sheraton McKinney Hotel   
2      -96.59469                           The Grand Hotel McKinney   
3      -96.59469  Courtyard Dallas Allen at the John Q. Hammons ...   
4      -96.59469                                   TownPlace Suites   

                                       Venue Address  Venue Latitude  \
0  [1500 Industrial Blvd, McKinney, TX 75069, Uni...       33.177463   
1  [1900 Gateway Blvd, McKinney, TX 75070, United...       33.162836   
2  [114 W Louisiana St, McKinney, TX 75069, Unite...       33.197335   
3  [210 East Stacy Road (at Andrews Pkwy), Allen,...       33.128486   
4                      [McKinney, TX, United States]       33.168321   

   Venue Longitude Venue Category               Category ID  
0       -96.592294        Airport  4d4b7105d754a06379d81259  
1       -96.641142          Hotel  4d4b7105d754a06379d81259  
2       -96.616334          Hotel  4d4b7105d754a06379d81259  
3       -96.654636          Hotel  4d4b7105d754a06379d81259  
4       -96.636884          Hotel  4d4b7105d754a06379d81259

In [168]:
# Defining NEW function for getting Nearby Venues
def getNearbyVenuesNEW(City_Index,
                    City,
                    State,
                    zipcode,
                    Population,
                    latitudes,
                    longitudes,
                    search_radius,
                    category_id):
    
    venues_list=[]
    for City_Index, City, State, zipcode, Population, lat, lng, search_radius in zip(City_Index, City, State, zipcode, Population, latitudes, longitudes, search_radius):
        print(zipcode)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&categoryId={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            search_radius,
            category_id,
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        for v in results:
            try: venues_list.append([(City_Index,
                             City,
                             State,
                             zipcode,
                             Population, 
                             lat,
                             lng,
                             v['venue']['name'],
                             v['venue']['location']['formattedAddress'],
                             v['venue']['location']['lat'],
                             v['venue']['location']['lng'],
                             v['venue']['categories'][0]['name'],
                             category_id)])
            except: venues_list.append([(City_Index,
                             City,
                             State,
                             zipcode,
                             Population, 
                             lat,
                             lng,
                             v['venue']['name'],
                             v['venue']['location']['formattedAddress'],
                             v['venue']['location']['lat'],
                             v['venue']['location']['lng'],
                                         'Category Not Found', # Handles a missing category in the venues list.
                                         category_id)])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['City_Index','City','State','ZIP','ZIP Population','ZIP Latitude','ZIP Longitude','Venue','Venue Address','Venue Latitude','Venue Longitude','Venue Category','Category ID']
    
    return(nearby_venues)

In [170]:
# Creating dataframe for nearby Professional & Other Places venues in each zip code:
df_professional = getNearbyVenuesNEW(City_Index=df_zips['City_Index'],
                                        City=df_zips['City'],
                                        State=df_zips['State'],
                                        zipcode=df_zips['ZIP'],
                                        Population=df_zips['Population'],
                                        latitudes=df_zips['lat'],
                                        longitudes=df_zips['lng'],
                                        search_radius=df_zips['Radius m'],
                            category_id='4d4b7105d754a06375d81259') # Professional & Other Places
df_professional.head()

75069
75070
75071
27511
27513
27518
27519
76541
76542
76543
76549
80521
80524
80525
80526
80528
98660
98661
98662
98663
98664
98665
98682
98683
98684
98685
98686
91761
91762
91764
97301
97302
97303
97304
97305
97306
97317
66061
66062
94541
94542
94544
94545
78501
78503
78504
32601
32603
32605
32606
32607
32608
32609
32612
32641
32653
70501
70503
70506
70507
70508
75149
75150
75181
47708
47710
47711
47712
47713
47714
47715
47720
47725
91360
91362
60431
60432
60433
60435
60436
45402
45403
45404
45405
45406
45409
45410
45414
45415
45416
45417
45419
45420
45424
45426
45428
45429
45430
45431
45432
45433
45434
45439
45440
45449
45458
45459
66603
66604
66605
66606
66607
66608
66609
66610
66611
66612
66614
66615
66616
66617
66618
66619
66621
66622
62701
62702
62703
62704
62707
62711
62712
23661
23663
23664
23665
23666
23669
61602
61603
61604
61605
61606
61607
61614
61615
61625
61101
61102
61103
61104
61107
61108
61109
61112
61114


City_Index      City  State    ZIP  ZIP Population  ZIP Latitude  \
0           0  McKinney  Texas  75069           37834      33.16547   
1           0  McKinney  Texas  75069           37834      33.16547   
2           0  McKinney  Texas  75069           37834      33.16547   
3           0  McKinney  Texas  75069           37834      33.16547   
4           0  McKinney  Texas  75069           37834      33.16547   

   ZIP Longitude                        Venue  \
0      -96.59469  Heritage Ranch Country Club   
1      -96.59469      Sheraton McKinney Hotel   
2      -96.59469             Wells Fargo Bank   
3      -96.59469     McKinney Garage Door Man   
4      -96.59469             Wells Fargo Bank   

                                       Venue Address  Venue Latitude  \
0                      [Fairview, TX, United States]       33.138340   
1  [1900 Gateway Blvd, McKinney, TX 75070, United...       33.162836   
2  [1775 Eldorado Pkwy, McKinney, TX 75069, Unite...       33.172437   
3      [McKinney, McKinney, TX 75069, United States]       33.196412   
4  [1602 E Exchange Pkwy (Angel), Allen, TX 75002...       33.114457   

   Venue Longitude Venue Category               Category ID  
0       -96.593801       Building  4d4b7105d754a06375d81259  
1       -96.641142          Hotel  4d4b7105d754a06375d81259  
2       -96.635982           Bank  4d4b7105d754a06375d81259  
3       -96.608255   Home Service  4d4b7105d754a06375d81259  
4       -96.628186           Bank  4d4b7105d754a06375d81259

Now we have all of the data we need! Let's find out how many rows exist in each dataframe.

In [171]:
print('Arts & Entertainment:',df_arts_entertainment.shape[0])
print('College & University:',df_college_university.shape[0])
print('Event:',df_event.shape[0])
print('Food:',df_food.shape[0])
print('Nightlife Spots:',df_nightlife.shape[0])
print('Outdoors & Recreation:',df_outdoors_recreation.shape[0])
print('Residence:',df_residence.shape[0])
print('Shop & Service:',df_shop_service.shape[0])
print('Travel & Transport:',df_travel_transport.shape[0])
print('Professional & Other Places:',df_professional.shape[0])

Arts & Entertainment: 2225
College & University: 4877
Event: 157
Food: 11115
Nightlife Spots: 3052
Outdoors & Recreation: 8151
Residence: 2622
Shop & Service: 14422
Travel & Transport: 5620
Professional & Other Places: 13289


The variation in dataframe row counts is a very good indicator that we will find significant variation in the employer portfolios of each city in our set. But we still have some cleaning to do.

In [172]:
# Let's concatenate the existing dataframes.
dataframe_list = [df_arts_entertainment,
                  df_college_university,
                  df_event,
                  df_food,
                  df_nightlife,
                  df_outdoors_recreation,
                  df_residence,
                  df_shop_service,
                  df_travel_transport,
                  df_professional]

df_city_businesses = pd.concat(dataframe_list)
df_city_businesses.shape

(65530, 13)

In [173]:
# Now let's eliminate duplicates where Foursquare returned results outside of the specified coordinates' zip codes.
df_city_businesses.reset_index(drop=True,inplace=True)
df_city_businesses['ZIP']=df_city_businesses['ZIP'].astype(str)
df_city_businesses['Venue Address']=df_city_businesses['Venue Address'].astype(str)
df_city_businesses['ZIP in Address'] = [x[0] in x[1] for x in zip(df_city_businesses['ZIP'], df_city_businesses['Venue Address'])]
df_city_businesses=df_city_businesses[df_city_businesses['ZIP in Address'] == True] # Filtering out search results outside of zip codes.
df_city_businesses

City_Index      City     State    ZIP  ZIP Population  ZIP Latitude  \
0               0  McKinney     Texas  75069           37834      33.16547   
1               0  McKinney     Texas  75069           37834      33.16547   
5               0  McKinney     Texas  75069           37834      33.16547   
8               0  McKinney     Texas  75069           37834      33.16547   
9               0  McKinney     Texas  75069           37834      33.16547   
...           ...       ...       ...    ...             ...           ...   
65518          21  Rockford  Illinois  61114           15591      42.30841   
65519          21  Rockford  Illinois  61114           15591      42.30841   
65524          21  Rockford  Illinois  61114           15591      42.30841   
65525          21  Rockford  Illinois  61114           15591      42.30841   
65526          21  Rockford  Illinois  61114           15591      42.30841   

       ZIP Longitude                            Venue  \
0          -96.59469  McKinney Performing Arts Center   
1          -96.59469           iPic Theaters Fairview   
5          -96.59469                 Heard-Craig Hall   
8          -96.59469            Dancer Strong Academy   
9          -96.59469           McKinney Dance Academy   
...              ...                              ...   
65518      -88.99096         Walmart Vision & Glasses   
65519      -88.99096       Forest City Baptist Church   
65524      -88.99096        Carlson Elementary School   
65525      -88.99096                       Dr. Larson   
65526      -88.99096             David D. Larson, DMD   

                                           Venue Address  Venue Latitude  \
0      ['111 N Tennessee St (btwn W Virginia & W Loui...       33.197630   
1      ['321 Town Pl', 'Fairview, TX 75069', 'United ...       33.132561   
5      ['306 N Church St', 'McKinney, TX 75069', 'Uni...       33.199419   
8      ['192 Industrial Blvd #103 (Near 75 and 121)',...       33.178848   
9      ['901 Elm St', 'McKinney, TX 75069', 'United S...       33.185380   
...                                                  ...             ...   
65518  ['3849 Northridge Dr', 'Rockford, IL 61114', '...       42.315140   
65519  ['4241 Pepper Dr', 'Rockford, IL 61114', 'Unit...       42.306646   
65524  ['4015 Pepper Dr (at Pecan St.)', 'Rockford, I...       42.306817   
65525  ['6415 Forest Hills Rd', 'Rockford, IL 61114',...       42.314613   
65526  ['6415 Forest Hills Rd', 'Rockford, IL 61114',...       42.314613   

       Venue Longitude     Venue Category               Category ID  \
0           -96.615563            Theater  4d4b7104d754a06370d81259   
1           -96.647687      Movie Theater  4d4b7104d754a06370d81259   
5           -96.617083            Theater  4d4b7104d754a06370d81259   
8           -96.612324       Dance Studio  4d4b7104d754a06370d81259   
9           -96.607610       Dance Studio  4d4b7104d754a06370d81259   
...                ...                ...                       ...   
65518       -89.031952       Optical Shop  4d4b7105d754a06375d81259   
65519       -89.033345             Church  4d4b7105d754a06375d81259   
65524       -89.034946  Elementary School  4d4b7105d754a06375d81259   
65525       -89.034241   Dentist's Office  4d4b7105d754a06375d81259   
65526       -89.034241   Dentist's Office  4d4b7105d754a06375d81259   

       ZIP in Address  
0                True  
1                True  
5                True  
8                True  
9                True  
...               ...  
65518            True  
65519            True  
65524            True  
65525            True  
65526            True  

[21993 rows x 14 columns]

In [174]:
df_city_businesses.reset_index(drop=True,inplace=True)

In [230]:
# Let's create a dataframe column that returns the top-level category names corresponding to each Category ID.
# Creating a dictionary with mapping values:
category_id_dict = {'4d4b7104d754a06370d81259': 'Arts & Entertainment',
                    '4d4b7105d754a06372d81259': 'College & University',
                    '4d4b7105d754a06373d81259': 'Event',
                    '4d4b7105d754a06374d81259': 'Food',
                    '4d4b7105d754a06376d81259': 'Nightlife Spot',
                    '4d4b7105d754a06377d81259': 'Outdoors & Recreation',
                    '4d4b7105d754a06375d81259': 'Professional & Other Places',
                    '4e67e38e036454776db1fb3a': 'Residence',
                    '4d4b7105d754a06378d81259': 'Shop & Service',
                    '4d4b7105d754a06379d81259': 'Travel & Transport'}
df_city_businesses['Venue Top Category'] = df_city_businesses['Category ID'].map(category_id_dict) # Mapping to new column.
df_city_businesses.head()

City_Index      City  State    ZIP  ZIP Population  ZIP Latitude  \
0           0  McKinney  Texas  75069           37834      33.16547   
1           0  McKinney  Texas  75069           37834      33.16547   
2           0  McKinney  Texas  75069           37834      33.16547   
3           0  McKinney  Texas  75069           37834      33.16547   
4           0  McKinney  Texas  75069           37834      33.16547   

   ZIP Longitude                            Venue  \
0      -96.59469  McKinney Performing Arts Center   
1      -96.59469           iPic Theaters Fairview   
2      -96.59469                 Heard-Craig Hall   
3      -96.59469            Dancer Strong Academy   
4      -96.59469           McKinney Dance Academy   

                                       Venue Address  Venue Latitude  \
0  ['111 N Tennessee St (btwn W Virginia & W Loui...       33.197630   
1  ['321 Town Pl', 'Fairview, TX 75069', 'United ...       33.132561   
2  ['306 N Church St', 'McKinney, TX 75069', 'Uni...       33.199419   
3  ['192 Industrial Blvd #103 (Near 75 and 121)',...       33.178848   
4  ['901 Elm St', 'McKinney, TX 75069', 'United S...       33.185380   

   Venue Longitude Venue Category               Category ID  ZIP in Address  \
0       -96.615563        Theater  4d4b7104d754a06370d81259            True   
1       -96.647687  Movie Theater  4d4b7104d754a06370d81259            True   
2       -96.617083        Theater  4d4b7104d754a06370d81259            True   
3       -96.612324   Dance Studio  4d4b7104d754a06370d81259            True   
4       -96.607610   Dance Studio  4d4b7104d754a06370d81259            True   

     Venue Top Category  
0  Arts & Entertainment  
1  Arts & Entertainment  
2  Arts & Entertainment  
3  Arts & Entertainment  
4  Arts & Entertainment

In [231]:
# Let's save this data to an Excel file so we don't accidentally lose it!
excel_export_path = r'D:\Documents\Data Science\Capstone Project\CityBusinessesExport.xlsx'
df_city_businesses.to_excel(excel_export_path,sheet_name='City Businesses')

In [232]:
# Let's create a new dataframe with just the columns we need for analysis.
columns_new = ['City_Index','City','State','ZIP','ZIP Population','Venue','Venue Category','Venue Top Category']
df_biz_analysis = df_city_businesses[columns_new].copy()
df_biz_analysis.head()

City_Index      City  State    ZIP  ZIP Population  \
0           0  McKinney  Texas  75069           37834   
1           0  McKinney  Texas  75069           37834   
2           0  McKinney  Texas  75069           37834   
3           0  McKinney  Texas  75069           37834   
4           0  McKinney  Texas  75069           37834   

                             Venue Venue Category    Venue Top Category  
0  McKinney Performing Arts Center        Theater  Arts & Entertainment  
1           iPic Theaters Fairview  Movie Theater  Arts & Entertainment  
2                 Heard-Craig Hall        Theater  Arts & Entertainment  
3            Dancer Strong Academy   Dance Studio  Arts & Entertainment  
4           McKinney Dance Academy   Dance Studio  Arts & Entertainment

In [233]:
# Grouping by ZIP code for venue counts in each ZIP:
df_zip_venue_counts = df_biz_analysis.copy().groupby('ZIP').count()
df_zip_venue_counts_drop = ['City_Index','City','State','ZIP Population','Venue Category','Venue Top Category']
df_zip_venue_counts.drop(df_zip_venue_counts_drop,axis=1,inplace=True)
df_zip_venue_counts

Venue
ZIP         
23661    136
23663    117
23664     23
23665     58
23666    268
...      ...
98682    116
98683    215
98684    238
98685    109
98686    183

[155 rows x 1 columns]

In [234]:
# Let's see how many unique bottom-level venue categories exist in the df_biz_analysis dataframe:
print('There are {} unique categories.'.format(len(df_biz_analysis['Venue Category'].unique())))

There are 529 unique categories.


In [235]:
# One-hot encoding for bottom-level venue types in each ZIP:

df_biz_bottom = df_biz_analysis.copy()
df_biz_bottom.drop('Venue Top Category',axis=1,inplace = True)
# one hot encoding
df_biz_bottom_onehot = pd.get_dummies(df_biz_bottom[['Venue Category']], prefix="", prefix_sep="")

# add ZIP column back to dataframe
df_biz_bottom_onehot['ZIP'] = df_biz_bottom['ZIP'] 

# Reordering the neighborhood column to be listed first
cols = df_biz_bottom_onehot.columns.tolist()
cols.remove('ZIP')
cols_reordered = ['ZIP']
cols_reordered.extend(cols)
df_biz_bottom_onehot = df_biz_bottom_onehot[cols_reordered]
df_biz_bottom_onehot.head()

ZIP  ATM  Accessories Store  Acupuncturist  Adult Boutique  \
0  75069    0                  0              0               0   
1  75069    0                  0              0               0   
2  75069    0                  0              0               0   
3  75069    0                  0              0               0   
4  75069    0                  0              0               0   

   Adult Education Center  Advertising Agency  Airfield  Airport  \
0                       0                   0         0        0   
1                       0                   0         0        0   
2                       0                   0         0        0   
3                       0                   0         0        0   
4                       0                   0         0        0   

   Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0                   0               0                0                 0   
1                   0               0                0                 0   
2                   0               0                0                 0   
3                   0               0                0                 0   
4                   0               0                0                 0   

   Alternative Healer  American Restaurant  Amphitheater  Andhra Restaurant  \
0                   0                    0             0                  0   
1                   0                    0             0                  0   
2                   0                    0             0                  0   
3                   0                    0             0                  0   
4                   0                    0             0                  0   

   Animal Shelter  Antique Shop  Arcade  Arepa Restaurant  \
0               0             0       0                 0   
1               0             0       0                 0   
2               0             0       0                 0   
3               0             0       0                 0   
4               0             0       0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Art Studio  \
0                       0            0           0           0   
1                       0            0           0           0   
2                       0            0           0           0   
3                       0            0           0           0   
4                       0            0           0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Assisted Living  Astrologer  Athletics & Sports  Auditorium  \
0                0           0                   0           0   
1                0           0                   0           0   
2                0           0                   0           0   
3                0           0                   0           0   
4                0           0                   0           0   

   Australian Restaurant  Auto Dealership  Auto Garage  Auto Workshop  \
0                      0                0            0              0   
1                      0                0            0              0   
2                      0                0            0              0   
3                      0                0            0              0   
4                      0                0            0              0   

   Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Ballroom  Bank  \
0                0          0           0           0       0         0     0   
1                0          0           0           0       0         0     0   
2                0   

In [236]:
#Finding proportions of each bottom-level venue type within each ZIP:
df_biz_bottom_grouped = df_biz_bottom_onehot.groupby('ZIP').mean().reset_index()
df_biz_bottom_grouped.head()

ZIP       ATM  Accessories Store  Acupuncturist  Adult Boutique  \
0  23661  0.007353                0.0            0.0             0.0   
1  23663  0.000000                0.0            0.0             0.0   
2  23664  0.000000                0.0            0.0             0.0   
3  23665  0.000000                0.0            0.0             0.0   
4  23666  0.000000                0.0            0.0             0.0   

   Adult Education Center  Advertising Agency  Airfield   Airport  \
0                     0.0            0.007353       0.0  0.000000   
1                     0.0            0.000000       0.0  0.008547   
2                     0.0            0.000000       0.0  0.000000   
3                     0.0            0.000000       0.0  0.000000   
4                     0.0            0.000000       0.0  0.000000   

   Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0                 0.0             0.0         0.000000               0.0   
1                 0.0             0.0         0.000000               0.0   
2                 0.0             0.0         0.000000               0.0   
3                 0.0             0.0         0.000000               0.0   
4                 0.0             0.0         0.003731               0.0   

   Alternative Healer  American Restaurant  Amphitheater  Andhra Restaurant  \
0                 0.0             0.007353           0.0                0.0   
1                 0.0             0.017094           0.0                0.0   
2                 0.0             0.000000           0.0                0.0   
3                 0.0             0.000000           0.0                0.0   
4                 0.0             0.014925           0.0                0.0   

   Animal Shelter  Antique Shop  Arcade  Arepa Restaurant  \
0             0.0      0.000000     0.0               0.0   
1             0.0      0.008547     0.0               0.0   
2             0.0      0.000000     0.0               0.0   
3             0.0      0.000000     0.0               0.0   
4             0.0      0.000000     0.0               0.0   

   Argentinian Restaurant  Art Gallery  Art Museum  Art Studio  \
0                     0.0          0.0         0.0         0.0   
1                     0.0          0.0         0.0         0.0   
2                     0.0          0.0         0.0         0.0   
3                     0.0          0.0         0.0         0.0   
4                     0.0          0.0         0.0         0.0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0             0.000000                   0.0          0.000000   
1             0.008547                   0.0          0.008547   
2             0.000000                   0.0          0.000000   
3             0.000000                   0.0          0.000000   
4             0.003731                   0.0          0.000000   

   Assisted Living  Astrologer  Athletics & Sports  Auditorium  \
0              0.0         0.0            0.000000         0.0   
1              0.0         0.0            0.000000         0.0   
2              0.0         0.0            0.000000         0.0   
3              0.0         0.0            0.000000         0.0   
4              0.0         0.0            0.003731         0.0   

   Australian Restaurant  Auto Dealership  Auto Garage  Auto Workshop  \
0                    0.0              0.0     0.000000       0.014706   
1                    0.0              0.0     0.008547       0.000000   
2                    0.0              0.0     0.000000       0.000000   
3                    0.0              0.0     0.000000       0.000000   
4                    0.0              0.0     0.000000       0.000000   

   Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Ballroom  Bank  \
0              0.0   0.000000         0.0         0.0     0.0       0.0   0.0   
1              0.0   0.000000         0.0         0.0     0.0     

In [244]:
# Let's save this data to an Excel file so we don't accidentally lose it!
excel_export_path_bottom = r'D:\Documents\Data Science\Capstone Project\CityBusinessesBottomExport.xlsx'
df_biz_bottom_grouped.to_excel(excel_export_path_bottom,sheet_name='City Businesses Bottom')

In [240]:
# One-hot encoding for top-level venue types in each ZIP:

df_biz_top = df_biz_analysis.copy()
df_biz_top.drop('Venue Category',axis=1,inplace = True)
# one hot encoding
df_biz_top_onehot = pd.get_dummies(df_biz_top[['Venue Top Category']], prefix="", prefix_sep="")

# add ZIP column back to dataframe
df_biz_top_onehot['ZIP'] = df_biz_top['ZIP'] 

# Reordering the neighborhood column to be listed first
cols_top = df_biz_top_onehot.columns.tolist()
cols_top.remove('ZIP')
cols_top_reordered = ['ZIP']
cols_top_reordered.extend(cols_top)
df_biz_top_onehot = df_biz_top_onehot[cols_top_reordered]
df_biz_top_onehot.head()

ZIP  Arts & Entertainment  College & University  Event  Food  \
0  75069                     1                     0      0     0   
1  75069                     1                     0      0     0   
2  75069                     1                     0      0     0   
3  75069                     1                     0      0     0   
4  75069                     1                     0      0     0   

   Nightlife Spot  Outdoors & Recreation  Professional & Other Places  \
0               0                      0                            0   
1               0                      0                            0   
2               0                      0                            0   
3               0                      0                            0   
4               0                      0                            0   

   Residence  Shop & Service  Travel & Transport  
0          0               0                   0  
1          0               0                   0  
2          0               0                   0  
3          0               0                   0  
4          0               0                   0

In [241]:
#Finding proportions of each top-level venue type within each ZIP:
df_biz_top_grouped = df_biz_top_onehot.groupby('ZIP').mean().reset_index()
df_biz_top_grouped.head()

ZIP  Arts & Entertainment  College & University     Event      Food  \
0  23661              0.007353              0.000000  0.000000  0.088235   
1  23663              0.017094              0.034188  0.000000  0.188034   
2  23664              0.000000              0.000000  0.000000  0.000000   
3  23665              0.034483              0.017241  0.000000  0.120690   
4  23666              0.026119              0.063433  0.003731  0.167910   

   Nightlife Spot  Outdoors & Recreation  Professional & Other Places  \
0        0.022059               0.029412                     0.375000   
1        0.034188               0.034188                     0.205128   
2        0.043478               0.173913                     0.173913   
3        0.034483               0.172414                     0.396552   
4        0.037313               0.097015                     0.201493   

   Residence  Shop & Service  Travel & Transport  
0   0.007353        0.455882            0.014706  
1   0.017094        0.444444            0.025641  
2   0.043478        0.521739            0.043478  
3   0.000000        0.172414            0.051724  
4   0.059701        0.201493            0.141791

In [245]:
# Let's save this data to an Excel file so we don't accidentally lose it!
excel_export_path_top = r'D:\Documents\Data Science\Capstone Project\CityBusinessesTopExport.xlsx'
df_biz_top_grouped.to_excel(excel_export_path_top,sheet_name='City Businesses Top')

Now we have two dataframes, **df_biz_bottom_grouped** and **df_biz_top_grouped**, which show proportions of business types within each zip code. The former provides extremely granular categorization of business types, whereas the latter zooms out to broader categorizations. Since the top-level grouping has many more data points corresponding to each proportion value, my assumption is that it will be more useful for city population growth inferences. That said, the bottom-level grouping may expose particular proportion values of interest that would otherwise be hidden in the aggregates.

At this point, we now need to roll up the zip-level business proportions into city-level business proportions. The question though is how the proportions should be weighted for each zip code:
1. On one hand, we could choose to weight the proportion values by the percentage of city population within each zip code - this method assumes that population growth is most strongly driven by businesses that are co-located in the same zip codes as residents.
2. On second hand, we could ignore the above method entirely and weight all city zip codes equally.
3. On the third hand, we could adopt a hybrid approach where the above two models are weighted and then combined.

In considering which method to use, tt's important to note that the average commuting distance in the United States is **19.7 miles**. Reviewing the uszips data set, we also know that the average diameter of each city zip code in our study is **7.3 miles**. We know from our QuickFact correlations earlier that there is a positive correlation between population growth and two job-related measures: the median household income and the proportion of people in the civilian labor force. This strongly implies that on average, **the majority of population residing within a given zip code is working in another zip code** nearby.

Based on that, we will use the 2nd method and weight all city zip codes equally, so as to avoid unintentionally biasing the business proportions.

In [321]:
# Let's create a copy of the df_biz_bottom_grouped and df_biz_top_grouped dataframes, then add the City_Index column to each.
df_biz_bottom_city=df_biz_bottom_grouped.copy()
df_biz_top_city=df_biz_top_grouped.copy()

df_zips['ZIP']=df_zips['ZIP'].astype(str) # Converting ZIP column in df_zips to string type to allow .merge.

df_biz_bottom_city=df_biz_bottom_city.merge(df_zips[['City_Index', 'ZIP']], on=['ZIP'])

df_biz_top_city=df_biz_top_city.merge(df_zips[['City_Index', 'ZIP']], on=['ZIP'])

In [360]:
# Now let's average the proportion values for each zip, grouped by City_Index.
df_biz_bottom_city_grouped=df_biz_bottom_city.copy()
df_biz_top_city_grouped=df_biz_top_city.copy()

df_biz_bottom_city_grouped.drop('ZIP',axis=1,inplace=True)
df_biz_top_city_grouped.drop('ZIP',axis=1,inplace=True)

df_biz_bottom_city_grouped.set_index('City_Index',inplace=True)
df_biz_bottom_city_grouped_static=df_biz_bottom_city_grouped.groupby('City_Index').mean().copy()
df_biz_bottom_city_grouped_static.reset_index(inplace=True)
df_biz_bottom_city_grouped_static.head()

City_Index       ATM  Accessories Store  Acupuncturist  Adult Boutique  \
0           0  0.000000           0.000000       0.000000        0.000000   
1           1  0.000000           0.002753       0.001033        0.000000   
2           2  0.000000           0.000000       0.001289        0.000000   
3           3  0.001176           0.000000       0.000000        0.000000   
4           4  0.002330           0.000000       0.000365        0.000365   

   Adult Education Center  Advertising Agency  Airfield   Airport  \
0                     0.0            0.000000       0.0  0.001852   
1                     0.0            0.000000       0.0  0.000000   
2                     0.0            0.000000       0.0  0.003953   
3                     0.0            0.002565       0.0  0.000697   
4                     0.0            0.001123       0.0  0.000000   

   Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0            0.000000             0.0         0.000000          0.003704   
1            0.000000             0.0         0.000000          0.000000   
2            0.001984             0.0         0.001289          0.007937   
3            0.000000             0.0         0.000833          0.001389   
4            0.000000             0.0         0.000000          0.000000   

   Alternative Healer  American Restaurant  Amphitheater  Andhra Restaurant  \
0            0.002778             0.008322      0.000000           0.000000   
1            0.000000             0.013741      0.002796           0.000000   
2            0.000000             0.004546      0.000000           0.000000   
3            0.000833             0.015772      0.000000           0.000000   
4            0.000000             0.007039      0.000000           0.000423   

   Animal Shelter  Antique Shop  Arcade  Arepa Restaurant  \
0             0.0      0.001852     0.0               0.0   
1             0.0      0.000000     0.0               0.0   
2             0.0      0.002336     0.0               0.0   
3             0.0      0.000000     0.0               0.0   
4             0.0      0.000000     0.0               0.0   

   Argentinian Restaurant  Art Gallery  Art Museum  Art Studio  \
0                     0.0     0.011557     0.00000         0.0   
1                     0.0     0.005192     0.00000         0.0   
2                     0.0     0.000000     0.00000         0.0   
3                     0.0     0.010343     0.00201         0.0   
4                     0.0     0.000876     0.00000         0.0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0             0.001383              0.000000          0.007396   
1             0.002753              0.002525          0.005896   
2             0.001289              0.000000          0.003866   
3             0.002707              0.001530          0.003262   
4             0.004600              0.000000          0.002664   

   Assisted Living  Astrologer  Athletics & Sports  Auditorium  \
0         0.011100         0.0            0.000000    0.000000   
1         0.007345         0.0            0.005363    0.000000   
2         0.000000         0.0            0.001289    0.002336   
3         0.005287         0.0            0.007843    0.000000   
4         0.011162         0.0            0.009737    0.000000   

   Australian Restaurant  Auto Dealership  Auto Garage  Auto Workshop  \
0               0.000000         0.000000     0.000000       0.000000   
1               0.000000         0.001220     0.000000       0.000000   
2               0.000000         0.000000     0.000000       0.000000   
3               0.001176         0.000697     0.000000       0.000000   
4               0.000000         0.000000     0.001327       0.000365   

   Automotive Shop  BBQ Joint  Baby Store  Bagel Shop    Bakery  Ballroom  \
0         0.005087   0.001852    0.000000    0.001383  0.003235       0.0   
1         0.011089   0.002296    0.000000 

In [350]:
df_biz_top_city_grouped.set_index('City_Index',inplace=True)
df_biz_top_city_grouped_static=df_biz_top_city_grouped.groupby('City_Index').mean().copy()
df_biz_top_city_grouped_static.reset_index(inplace=True)
df_biz_top_city_grouped_static.head()

City_Index  Arts & Entertainment  College & University     Event      Food  \
0           0              0.055955              0.033299  0.003235  0.152559   
1           1              0.039519              0.026008  0.004287  0.174498   
2           2              0.019813              0.072707  0.003937  0.187008   
3           3              0.059027              0.067242  0.001530  0.141026   
4           4              0.012445              0.041318  0.001149  0.151269   

   Nightlife Spot  Outdoors & Recreation  Professional & Other Places  \
0        0.039780               0.140030                     0.238589   
1        0.044560               0.155488                     0.240981   
2        0.022334               0.067943                     0.202384   
3        0.056461               0.139717                     0.232109   
4        0.028120               0.123347                     0.248661   

   Residence  Shop & Service  Travel & Transport  
0   0.088762        0.122530            0.125261  
1   0.084327        0.182329            0.048003  
2   0.023552        0.279771            0.120551  
3   0.059379        0.165885            0.077623  
4   0.044241        0.263515            0.085936

In [354]:
df_cities_filtered.rename_axis('City_Index',inplace=True)
df_cities_filtered.head()

City           State  Pop 2019 Est  Pop 2010  \
City_Index                                                         
0               McKinney           Texas        199177    131117   
1                   Cary  North Carolina        170282    135234   
2                Killeen           Texas        151666    127921   
3           Fort Collins        Colorado        170243    143986   
4              Vancouver      Washington        184463    161791   

            2016 Land SqMi  Density 2010  Density 2019 Est  Pop Change Prop.  
City_Index                                                                    
0                     63.0   2081.222222       3161.539683            0.5191  
1                     56.5   2393.522124       3013.840708            0.2592  
2                     53.5   2391.046729       2834.878505            0.1856  
3                     55.8   2580.394265       3050.949821            0.1824  
4                     46.9   3449.701493       3933.113006            0.1401

In [355]:
df_cities_filtered.reset_index(inplace=True)
df_cities_filtered.head()

City_Index          City           State  Pop 2019 Est  Pop 2010  \
0           0      McKinney           Texas        199177    131117   
1           1          Cary  North Carolina        170282    135234   
2           2       Killeen           Texas        151666    127921   
3           3  Fort Collins        Colorado        170243    143986   
4           4     Vancouver      Washington        184463    161791   

   2016 Land SqMi  Density 2010  Density 2019 Est  Pop Change Prop.  
0            63.0   2081.222222       3161.539683            0.5191  
1            56.5   2393.522124       3013.840708            0.2592  
2            53.5   2391.046729       2834.878505            0.1856  
3            55.8   2580.394265       3050.949821            0.1824  
4            46.9   3449.701493       3933.113006            0.1401

In [361]:
df_biz_bottom_city_grouped_static = df_biz_bottom_city_grouped_static.merge(df_cities_filtered[['City_Index', 'City']], on=['City_Index'])
df_biz_bottom_city_grouped_static = df_biz_bottom_city_grouped_static.merge(df_cities_filtered[['City_Index', 'State']], on=['City_Index'])
df_biz_bottom_city_grouped_static = df_biz_bottom_city_grouped_static.merge(df_cities_filtered[['City_Index', 'Pop Change Prop.']], on=['City_Index'])
df_biz_bottom_city_grouped_static

City_Index       ATM  Accessories Store  Acupuncturist  Adult Boutique  \
0            0  0.000000           0.000000       0.000000        0.000000   
1            1  0.000000           0.002753       0.001033        0.000000   
2            2  0.000000           0.000000       0.001289        0.000000   
3            3  0.001176           0.000000       0.000000        0.000000   
4            4  0.002330           0.000000       0.000365        0.000365   
5            5  0.000000           0.000000       0.000000        0.000000   
6            6  0.000646           0.003571       0.001534        0.000444   
7            7  0.001852           0.000000       0.000000        0.000000   
8            8  0.002883           0.001524       0.001174        0.000000   
9            9  0.000000           0.001328       0.000000        0.000000   
10          10  0.001300           0.002388       0.001138        0.000000   
11          11  0.000000           0.000000       0.000877        0.000000   
12          12  0.000000           0.000000       0.000000        0.000000   
13          13  0.000000           0.000000       0.000000        0.000000   
14          14  0.001730           0.005190       0.000000        0.000000   
15          15  0.011345           0.000000       0.000000        0.000000   
16          16  0.004272           0.001090       0.000283        0.000000   
17          17  0.005600           0.002912       0.000000        0.000000   
18          18  0.001556           0.000558       0.000558        0.000000   
19          19  0.001225           0.000000       0.000000        0.000000   
20          20  0.000000           0.000654       0.000000        0.000000   
21          21  0.004355           0.004364       0.000000        0.000000   

    Adult Education Center  Advertising Agency  Airfield   Airport  \
0                 0.000000            0.000000  0.000000  0.001852   
1                 0.000000            0.000000  0.000000  0.000000   
2                 0.000000            0.000000  0.000000  0.003953   
3                 0.000000            0.002565  0.000000  0.000697   
4                 0.000000            0.001123  0.000000  0.000000   
5                 0.000000            0.000000  0.000000  0.007937   
6                 0.000000            0.000000  0.000000  0.002409   
7                 0.000000            0.000000  0.000000  0.001852   
8                 0.000000            0.001174  0.000000  0.002347   
9                 0.000000            0.002545  0.000000  0.001727   
10                0.000000            0.000000  0.000000  0.004878   
11                0.000000            0.000000  0.000000  0.000877   
12                0.000000            0.006410  0.002208  0.000000   
13                0.000000            0.001221  0.000000  0.001019   
14                0.000000            0.001730  0.000000  0.000000   
15                0.000000            0.000000  0.000000  0.004444   
16                0.000128            0.001252  0.000000  0.000219   
17                0.000000            0.000427  0.000000  0.006131   
18                0.000000            0.003984  0.000000  0.016327   
19                0.000000            0.002146  0.000000  0.001425   
20                0.000000            0.002404  0.000000  0.003741   
21                0.000000            0.000426  0.000000  0.001837   

    Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0             0.000000        0.000000         0.000000          0.003704   
1             0.000000        0.000000         0.000000          0.000000   
2             0.001984        0.000000         0.001289          0.007937   
3             0.000000        0.000000         0.000833          0.001389   
4             0.000000        0.000000         0.000000          0.000000   
5             0.000000        0.003968         0.011905          0.017857   
6             0.000000        0.000000         0.002447    

In [362]:
df_biz_top_city_grouped_static = df_biz_top_city_grouped_static.merge(df_cities_filtered[['City_Index', 'City']], on=['City_Index'])
df_biz_top_city_grouped_static = df_biz_top_city_grouped_static.merge(df_cities_filtered[['City_Index', 'State']], on=['City_Index'])
df_biz_top_city_grouped_static = df_biz_top_city_grouped_static.merge(df_cities_filtered[['City_Index', 'Pop Change Prop.']], on=['City_Index'])
df_biz_top_city_grouped_static

City_Index  Arts & Entertainment  College & University     Event  \
0            0              0.055955              0.033299  0.003235   
1            1              0.039519              0.026008  0.004287   
2            2              0.019813              0.072707  0.003937   
3            3              0.059027              0.067242  0.001530   
4            4              0.012445              0.041318  0.001149   
5            5              0.027355              0.084013  0.003472   
6            6              0.020311              0.073981  0.000887   
7            7              0.041099              0.059140  0.001852   
8            8              0.020552              0.170250  0.000000   
9            9              0.030005              0.060315  0.007726   
10          10              0.018294              0.131294  0.000983   
11          11              0.043638              0.044097  0.002703   
12          12              0.016766              0.038435  0.002208   
13          13              0.023747              0.044624  0.006057   
14          14              0.040553              0.076885  0.000000   
15          15              0.019407              0.040766  0.000000   
16          16              0.019594              0.029205  0.000749   
17          17              0.033034              0.049635  0.000000   
18          18              0.026748              0.066394  0.001468   
19          19              0.021541              0.027431  0.000622   
20          20              0.037170              0.073299  0.001330   
21          21              0.025151              0.040024  0.000426   

        Food  Nightlife Spot  Outdoors & Recreation  \
0   0.152559        0.039780               0.140030   
1   0.174498        0.044560               0.155488   
2   0.187008        0.022334               0.067943   
3   0.141026        0.056461               0.139717   
4   0.151269        0.028120               0.123347   
5   0.210575        0.023828               0.076352   
6   0.136667        0.054537               0.120638   
7   0.164038        0.042473               0.140442   
8   0.150934        0.018141               0.124229   
9   0.199258        0.082074               0.110936   
10  0.120752        0.027169               0.136288   
11  0.167588        0.044207               0.104857   
12  0.162072        0.021249               0.104510   
13  0.167569        0.031520               0.113648   
14  0.181758        0.040553               0.149796   
15  0.122244        0.036435               0.102236   
16  0.160362        0.043380               0.086433   
17  0.112423        0.031182               0.061982   
18  0.192671        0.057694               0.111545   
19  0.125452        0.039637               0.103827   
20  0.160030        0.047560               0.072114   
21  0.176145        0.041377               0.089411   

    Professional & Other Places  Residence  Shop & Service  \
0                      0.238589   0.088762        0.122530   
1                      0.240981   0.084327        0.182329   
2                      0.202384   0.023552        0.279771   
3                      0.232109   0.059379        0.165885   
4                      0.248661   0.044241        0.263515   
5                      0.195271   0.034888        0.169294   
6                      0.195901   0.047129        0.290167   
7                      0.253405   0.036918        0.171027   
8                      0.188839   0.033101        0.201989   
9                      0.159018   0.028063        0.206296   
10                     0.178255   0.078883        0.234410   
11                     0.159136   0.050644        0.282907   
12                     0.250326   0.033880        0.301829   
13                     0.213129   0.045121        0.288357   
14                     0.185337   0.056974        0.234056   
15                     0.249209   0.025296        0.319177   
16                     0.26

In [364]:
# Let's save this data to an Excel file so we don't accidentally lose it!
excel_export_path_top_city = r'D:\Documents\Data Science\Capstone Project\CityTopAggregrateExport.xlsx'
df_biz_top_city_grouped_static.to_excel(excel_export_path_top_city,sheet_name='City Top Aggregate')

excel_export_path_bottom_city = r'D:\Documents\Data Science\Capstone Project\CityBottomAggregrateExport.xlsx'
df_biz_bottom_city_grouped_static.to_excel(excel_export_path_top_city,sheet_name='City Bottom Aggregate')

Now we are ready to determine which bottom-level and top-level business proportions correlate with population growth!

In [368]:
df_biz_bottom_corr = df_biz_bottom_city_grouped_static.corr()
df_biz_bottom_corr.sort_values('Pop Change Prop.',ascending = False, inplace = True) # Sorting
df_biz_bottom_corr['Pop Change Prop.'] # Filtering the correlation dataframe for values in the Pop Change Prop. column.

Pop Change Prop.                            1.000000
Bike Rental / Bike Share                    0.780697
Housing Development                         0.773556
Indoor Play Area                            0.771330
Christmas Market                            0.753363
Stables                                     0.753363
Travel & Transport                          0.753363
Swim School                                 0.736183
Irish Pub                                   0.725457
Cycle Studio                                0.686273
Pet Store                                   0.679617
Cable Car                                   0.674327
Fabric Shop                                 0.643803
Disc Golf                                   0.599093
Asian Restaurant                            0.594890
Automotive Shop                             0.557567
Warehouse Store                             0.552661
Moving Target                               0.550863
Gym                                         0.

**Wow!** The bottom-level correlations turned out to be very insightful! Some highlights:

Positive growth correlations:
1. Bike Rental / Bike Share - of all business categories - this one is most strongly correlated with population growth - Cycle Studio is not much further down the list. This likely reflects people settling into a new area and exploring their new surroundings. Bike Rentals / Shares are also a very modern and trendy technological offering that caters to younger (and growing) demographics.
2. Housing Development - This could reflect a combination of both high supply and also high demand. If housing is in greater demand, more housing suppliers will attempt to fill the gap. If housing is in great supply, the prices will be lower thereby attracting more people.
3. Indoor Play Area - Definitely reflects population growth!
4. Travel and Transport - More people, more travel. Infrastructure growth is needed to support a growing population.

Negative growth correlations:
1. Electronics store, construction & landscaping, furniture/home store, flower shop, and other repair shop - these all reflect more demand for home renovations in preparation for a home sale. 
3. Business service - this may reflect a maturing city where companies that need services are already established. Higher-growth cities would likely have a higher concentration of startups that are risky for business service providers.
2. Pawn shop - people are trying to get rid of their belongings and/or make a quick buck. It's not surprising to see these in economically-depressed areas where crime is high and populations are declining.
3. Lawyer! - I chuckled at this one. A concentration of lawyers could reflect a population in economic instability, where demand for ligitation is higher.

Now let's look at the top-level correlations.

In [369]:
df_biz_top_corr = df_biz_top_city_grouped_static.corr()
df_biz_top_corr.sort_values('Pop Change Prop.',ascending = False, inplace = True) # Sorting
df_biz_top_corr['Pop Change Prop.'] # Filtering the correlation dataframe for values in the Pop Change Prop. column.

Pop Change Prop.               1.000000
Residence                      0.689976
Arts & Entertainment           0.470641
Outdoors & Recreation          0.452558
Travel & Transport             0.424752
Event                          0.343142
Food                           0.072977
Professional & Other Places    0.010608
Nightlife Spot                 0.005056
College & University          -0.020197
Shop & Service                -0.734539
City_Index                    -0.864955
Name: Pop Change Prop., dtype: float64

The top-level correlation definitely echo the patterns observed in the bottom-level categories.

We see that residences have the strongest positive correlation, followed by arts/entertainment, outdoors/recreational, and travel/transport. On the opposite end, shops & service providers are strongly correlated with population decline, reflecting a maturing cities that are past their prime.

It's interesting to see that the College & University category has little if any correlation with population growth.

So where does Dayton, Ohio currently stand with respect to the top level categories? Let's find out.

In [380]:
df_biz_top_city_grouped_describe=df_biz_top_city_grouped_static.describe().copy()
df_biz_top_city_grouped_describe

City_Index  Arts & Entertainment  College & University      Event  \
count   22.000000             22.000000             22.000000  22.000000   
mean    10.500000              0.029624              0.061380   0.002028   
std      6.493587              0.012657              0.034325   0.002051   
min      0.000000              0.012445              0.026008   0.000000   
25%      5.250000              0.019937              0.040209   0.000654   
50%     10.500000              0.025950              0.054388   0.001399   
75%     15.750000              0.038932              0.073151   0.003102   
max     21.000000              0.059027              0.170250   0.007726   

            Food  Nightlife Spot  Outdoors & Recreation  \
count  22.000000       22.000000              22.000000   
mean    0.159859        0.039740               0.110717   
std     0.026292        0.014721               0.027019   
min     0.112423        0.018141               0.061982   
25%     0.143503        0.028886               0.092617   
50%     0.161217        0.040167               0.111240   
75%     0.175733        0.044471               0.133273   
max     0.210575        0.082074               0.155488   

       Professional & Other Places  Residence  Shop & Service  \
count                    22.000000  22.000000       22.000000   
mean                      0.218869   0.041956        0.254438   
std                       0.035895   0.020368        0.066805   
min                       0.159018   0.022415        0.122530   
25%                       0.190447   0.025964        0.203066   
50%                       0.217950   0.034384        0.271643   
75%                       0.249072   0.049765        0.312924   
max                       0.285160   0.088762        0.357033   

       Travel & Transport  Pop Change Prop.  
count           22.000000         22.000000  
mean             0.081389          0.084191  
std              0.034016          0.128940  
min              0.034088         -0.047500  
25%              0.055828         -0.006075  
50%              0.075648          0.061800  
75%              0.098158          0.128350  
max              0.174952          0.519100

In [379]:
df_biz_top_dayton = df_biz_top_city_grouped_static[df_biz_top_city_grouped_static['City']=='Dayton'].copy()
df_biz_top_dayton.drop(['City_Index','City','State'],axis=1,inplace=True)

In [397]:
df_biz_top_dayton.reset_index(drop=True,inplace=True)
df_biz_top_dayton

Arts & Entertainment  College & University     Event      Food  \
0              0.019594              0.029205  0.000749  0.160362   

   Nightlife Spot  Outdoors & Recreation  Professional & Other Places  \
0         0.04338               0.086433                     0.269232   

   Residence  Shop & Service  Travel & Transport  Pop Change Prop.  
0   0.025686        0.324086            0.041272           -0.0079

In [382]:
df_biz_top_city_grouped_describe.drop(['City_Index'],axis=1,inplace=True)

In [388]:
df_biz_top_city_grouped_describe.reset_index(inplace=True)

In [402]:
df_biz_top_city_mean = df_biz_top_city_grouped_describe[df_biz_top_city_grouped_describe['index']=='mean'].copy()
df_biz_top_city_mean.drop('index',axis=1,inplace=True)

In [403]:
df_biz_top_city_mean.reset_index(drop=True,inplace=True)
df_biz_top_dayton

Arts & Entertainment  College & University     Event      Food  \
0              0.019594              0.029205  0.000749  0.160362   

   Nightlife Spot  Outdoors & Recreation  Professional & Other Places  \
0         0.04338               0.086433                     0.269232   

   Residence  Shop & Service  Travel & Transport  Pop Change Prop.  
0   0.025686        0.324086            0.041272           -0.0079

In [407]:
# Let's find the differences between Dayton's business proportions and the mean city proportions.
df_biz_top_mean_delta = df_biz_top_dayton-df_biz_top_city_mean
df_biz_top_mean_delta

Arts & Entertainment  College & University     Event      Food  \
0              -0.01003             -0.032175 -0.001279  0.000503   

   Nightlife Spot  Outdoors & Recreation  Professional & Other Places  \
0        0.003641              -0.024284                     0.050362   

   Residence  Shop & Service  Travel & Transport  Pop Change Prop.  
0   -0.01627        0.069649           -0.040117         -0.092091

So what do these numbers above tell us? 
1. Compared to the *average* city in our set, Dayton currently has a lower proportion of unique businesses in the Residences, Arts/Entertainment, Outdoors/Recreation, and Travel/Transport categories. Based on the earlier correlations, shortages of these businesses could be both a driver and symptom of population decline.
2. Compared to the *average* city in our set, Dayton currently has a higher proportion of unique businesses in the Shop & Service categories - this likely reflects stagnation and/or decline in the local economy, as these business categories tend to thrive in low-churn, low-innovation environments requiring routine maintenance functions. On that last point, these types of businesses have strong incentives to reduce competition.

But how does Dayton compare to McKinney, Texas, the fastest growing city in the set?

In [406]:
df_biz_top_mckinney = df_biz_top_city_grouped_static[df_biz_top_city_grouped_static['City']=='McKinney'].copy()
df_biz_top_mckinney.drop(['City_Index','City','State'],axis=1,inplace=True)
df_biz_top_mckinney.reset_index(drop=True,inplace=True)
df_biz_top_mckinney

Arts & Entertainment  College & University     Event      Food  \
0              0.055955              0.033299  0.003235  0.152559   

   Nightlife Spot  Outdoors & Recreation  Professional & Other Places  \
0         0.03978                0.14003                     0.238589   

   Residence  Shop & Service  Travel & Transport  Pop Change Prop.  
0   0.088762         0.12253            0.125261            0.5191

In [409]:
df_biz_top_mckinney_delta=df_biz_top_dayton-df_biz_top_mckinney
df_biz_top_mckinney_delta

Arts & Entertainment  College & University     Event      Food  \
0             -0.036361             -0.004093 -0.002486  0.007803   

   Nightlife Spot  Outdoors & Recreation  Professional & Other Places  \
0          0.0036              -0.053597                     0.030642   

   Residence  Shop & Service  Travel & Transport  Pop Change Prop.  
0  -0.063076        0.201557           -0.083989            -0.527

1. Comparing Dayton to McKinney, we once again see that Dayton currently has a lower proportion of unique businesses in the Residences, Arts/Entertainment, Outdoors/Recreation, and Travel/Transport categories. In general, the magnitudes are higher compared to our earlier comparison against the mean proportions.
2. Compared to McKinney, Dayton has a much higher proportion of businesses in the Shop & Service categories. Again, the magnitude of difference is higher compared to our earlier comparison against the mean proportions.